# Calibration


   * [3D-cluster: $P_{T}$ resolution](#3D-cluster:-Pt-resolution)
   * [$p_{T}$ response](#$p_{T}$-response)


In [2]:
import sys
sys.path.insert(0, '..')
import ROOT
import root_numpy as rnp
import python.l1THistos as histos
import math
import uuid
import pandas as pd

ROOT.enableJSVis()
#ROOT.enableJSVis()

#from drawingTools import *

normalized_histos = list()
    

Welcome to JupyROOT 6.14/02


In [43]:
# %load ../drawingTools
import ROOT
import math
import uuid

# some useful globals, mainly to deal with ROOT idiosyncrasies
c_idx = 0
p_idx = 0
colors = range(1, 12)
stuff = []
f_idx = 0

ROOT.gStyle.SetOptTitle(False)
ROOT.gStyle.SetPadBottomMargin(0.13)
ROOT.gStyle.SetPadLeftMargin(0.13)
ROOT.gStyle.SetPadRightMargin(0.13)

# ROOT.gStyle.SetCanvasBorderMode(0)
# ROOT.gStyle.SetCanvasColor(0)


def getText(text, ndc_x, ndc_y):
    global stuff
    rtext = ROOT.TLatex(ndc_x, ndc_y, text)
    stuff.append(rtext)
    rtext.SetNDC(True)
    # rtext.SetTextFont(40)
    rtext.SetTextSize(0.03)
    return rtext

def getLegend(x1=0.7, y1=0.71, x2=0.95, y2=0.85):
    global stuff
    legend = ROOT.TLegend(x1, y1, x2, y2)
    stuff.append(legend)
    legend.SetFillColor(0)
    legend.SetFillStyle(0)
    legend.SetBorderSize(0)
    legend.SetTextSize(0.05)
    return legend

def newCanvas(name=None, title=None, height=600, width=800, xdiv=0, ydiv=0, form=4):
    global c_idx
    if name is None:
        name = 'c_{}'.format(uuid.uuid4().hex[:6])
        c_idx += 1
    if title is None:
        title = name
    # print name, title, width, height
    canvas = ROOT.TCanvas(name, title, width, height)
    if(xdiv*ydiv != 0):
        canvas.Divide(xdiv, ydiv)
    global stuff
    stuff.append(canvas)
    return canvas

def drawAndProfileX(plot2d, miny=None, maxy=None, do_profile=True, options='', text=None):
    global p_idx
    if miny and maxy:
        plot2d.GetYaxis().SetRangeUser(miny, maxy)
    c = newCanvas()
    c.SetGrid(1, 1)
    c.cd()
    plot2d.Draw(options)
    ROOT.gPad.SetGrid(1, 1)
    ROOT.gStyle.SetGridColor(15)

    if do_profile:
        profname = plot2d.GetName()+'_prof_'+str(p_idx)
        p_idx += 1
        firstbin = 1
        lastbin = -1
        prof = plot2d.ProfileX(profname, firstbin, lastbin, 's')
        prof.SetMarkerColor(2)
        prof.SetLineColor(2)
        prof.Draw('same')

    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw('same')

    c.Draw()


def draw(histograms,
         labels,
         options='',
         norm=False,
         logy=False,
         min_y=None,
         max_y=None,
         text=None,
         y_axis_label=None,
         x_axis_label=None,
         v_lines=None,
         h_lines=None,
         do_stats=False,
         do_profile=False,
         do_ratio=False):
    global colors
    global stuff
    global p_idx


    # 0 - determine kind and # of histos
    n_histos = len(histograms)
    if n_histos == 0:
        print '[draw]**ERROR: empy histo list'
        return

    histo_class = histograms[0].ClassName()

    # 1 - check argument consisntency
    if 'TH2' not in histo_class and do_profile:
        print '[draw]**ERROR: do_profile set for histo of class: {}'.format(histo_class)
        return

    # TH1 histograms are overlayed
    # TH2 histograms are drawn side by side in the same canvas
    overlay = True
    if n_histos > 1:
        if 'TH2' in histo_class or 'TH3' in histo_class:
            overlay = False

    # 2 - determine canvas properties
    xdiv = 0
    ydiv = 0
    c_width = 800
    c_height = 600
    # do_ratio = False

    if do_ratio:
        c_height = 800

    if not overlay:
        xdiv = 2
        c_width = 1000.
        ydiv = math.ceil(float(n_histos)/2)
        c_height = 500*ydiv
    canvas = newCanvas(name=None,
                       title=None,
                       height=int(c_height),
                       width=int(c_width),
                       xdiv=int(xdiv),
                       ydiv=int(ydiv))
    if overlay:
        canvas.SetRightMargin(0.30)

    canvas.cd()
    leg = getLegend()

    drawn_histos = []
    # drawn_histos = histograms
    for hidx, hist in enumerate(histograms):
        if 'TGraph' not in histo_class:
            hist.SetStats(do_stats)
        opt = options
        if overlay:
            hist.SetLineColor(colors[hidx])
            if hidx:
                opt = 'same,'+options
            else:
                if 'TGraph' in histo_class:
                    opt = options+'PA'
        else:
            canvas.cd(hidx+1)
        # print hidx, opt
        d_hist = hist
        if norm:
            d_hist = hist.DrawNormalized(opt, 1.)
        else:
            hist.Draw(opt)

        if do_profile:
            profname = d_hist.GetName()+'_prof_'+str(p_idx)
            p_idx += 1
            firstbin = 1
            lastbin = -1
            prof = d_hist.ProfileX(profname, firstbin, lastbin, 's')
            prof.SetMarkerColor(2)
            prof.SetLineColor(2)
            prof.Draw('same')

        if overlay:
            leg.AddEntry(hist, labels[hidx], 'l')
        else:
            if text:
                newtext = '{}: {}'.format(labels[hidx], text)
                rtext = getText(newtext, 0.15, 0.85)
                rtext.Draw('same')
        drawn_histos.append(d_hist)

    if do_ratio:
        h_ratio = ROOT.TRatioPlot(drawn_histos[0], drawn_histos[1])
        stuff.append(h_ratio)
        h_ratio.Draw()

        pad = canvas.cd(1)
        h_ratio.GetUpperPad().SetBottomMargin(0)
        h_ratio.GetUpperPad().SetRightMargin(0.3)
        if logy:
            h_ratio.GetUpperPad().SetLogy()
        pad.Update()
        pad = canvas.cd(2)
        h_ratio.GetLowerPad().SetTopMargin(0)
        h_ratio.GetLowerPad().SetRightMargin(0.3)
        pad.Update()
        # hratio.GetLowerRefGraph().GetYaxis().SetRangeUser(-6, 6)

    canvas.Update()

    # we now set the axis properties
    max_value = max_y
    min_value = min_y

    if min_y is None:
        min_value = min([hist.GetBinContent(hist.GetMinimumBin()) for hist in drawn_histos])
    if max_y is None:
        max_value = max([hist.GetBinContent(hist.GetMaximumBin()) for hist in drawn_histos])*1.2
    # print min_value, max_value

    for hist in drawn_histos:
        hist.GetYaxis().SetRangeUser(min_value, max_value)
        if y_axis_label:
            hist.GetYaxis().SetTitle(y_axis_label)
        if x_axis_label:
            hist.GetXaxis().SetTitle(x_axis_label)

    canvas.Draw()

    # we draw additional stuff if needed
    if overlay:
        canvas.cd()
        leg.Draw()
        if text:
            rtext = getText(text, 0.15, 0.85)
            rtext.Draw("same")

    pad_range = range(0, 1)
    if not overlay:
        pad_range = range(1, len(histograms)+1)

    for pad_id in pad_range:
        canvas.cd(pad_id)
        if v_lines:
            for v_line_x in v_lines:
                aline = ROOT.TLine(v_line_x, ROOT.gPad.GetUymin(), v_line_x,  ROOT.gPad.GetUymax())
                aline.SetLineStyle(2)
                aline.Draw("same")
                stuff.append(aline)
        if h_lines:
            for h_line_y in h_lines:
                aline = ROOT.TLine(ROOT.gPad.GetUxmin(), h_line_y, ROOT.gPad.GetUxmax(),  h_line_y)
                aline.SetLineStyle(2)
                aline.Draw("same")
                stuff.append(aline)
        if logy:
            if not do_ratio:
                ROOT.gPad.SetLogy()

        ROOT.gPad.Update()
    canvas.Update()
    canvas.Draw()

    return canvas


In [4]:
# %load samples.py
import ROOT
import pandas as pd
import python.selections as selections

version = 'v61t'

files = {}
file_keys = {}


class RootFile:
    def __init__(self, file_name):
        global file
        self.file_name = file_name
        if self.file_name not in files.keys():
            print 'get file: {}'.format(self.file_name)
            files[self.file_name] = ROOT.TFile(self.file_name)
        self._file = files[self.file_name]
        self._file_keys = None

    def cd(self):
        self._file.cd()

    def GetListOfKeys(self):
        global file_keys
        if self.file_name not in file_keys.keys():
            print 'get list'
            file_keys[self.file_name] = self._file.GetListOfKeys()
        self._file_keys = file_keys[self.file_name]
        return self._file_keys


class Sample():
    def __init__(self, name, label, version=None, type=None):
        self.name = name
        self.label = label
        if version:
            version = '_'+version
        else:
            version = ''
        self.histo_filename = '../plots1/histos_{}{}.root'.format(self.name, version)
        self.histo_file = ROOT.TFile(self.histo_filename, 'r')
        self.type = type


# sample_names = ['ele_flat2to100_PU0',
#                 'ele_flat2to100_PU200',
#                 'photonPt35_PU0',
#                 'photonPt35_PU200']


def get_label_dict(selections):
    dictionary = {}
    for sel in selections:
        dictionary[sel.name] = sel.label
    return dictionary


class HProxy:
    def __init__(self, classtype, tp, tp_sel, gen_sel, root_file):
        self.classtype = classtype
        self.tp = tp
        self.tp_sel = tp_sel
        self.gen_sel = gen_sel
        self.root_file = root_file
        self.instance = None

    def get(self):
        if self.instance is None:
            name = '{}_{}_{}'.format(self.tp, self.tp_sel, self.gen_sel)
            if self.gen_sel is None:
                name = '{}_{}'.format(self.tp, self.tp_sel)
            self.instance = self.classtype(name, self.root_file)
        return self.instance


class HPlot:
    def __init__(self, samples, tp_sets, tp_selections, gen_selections):
        self.tp_sets = tp_sets
        self.tp_selections = tp_selections
        self.gen_selections = gen_selections
        self.pus = []
        self.labels_dict = {}

        for sample in samples:
            self.pus.append(sample.label)
            self.labels_dict[sample.type] = sample.type

        self.data = pd.DataFrame(columns=['sample', 'pu', 'tp', 'tp_sel', 'gen_sel', 'classtype', 'histo'])

        self.labels_dict.update(tp_sets)
        self.labels_dict.update(tp_selections)
        self.labels_dict.update(gen_selections)
        self.labels_dict.update({'PU0': 'PU0', 'PU200': 'PU200'})

    def cache_histo(self,
                    classtype,
                    samples,
                    pus,
                    tps,
                    tp_sels,
                    gen_sels):
        if gen_sels is None:
            gen_sels = [None]

        for sample in samples:
            print sample
            for tp in tps:
                for tp_sel in tp_sels:
                    for gen_sel in gen_sels:
                        print sample, tp, tp_sel, gen_sel
                        self.data = self.data.append({'sample': sample.type,
                                                      'pu': sample.label,
                                                      'tp': tp,
                                                      'tp_sel': tp_sel,
                                                      'gen_sel': gen_sel,
                                                      'classtype': classtype,
                                                      'histo': HProxy(classtype, tp, tp_sel, gen_sel, sample.histo_file)},
                                                     ignore_index=True)

    def get_histo(self,
                  classtype,
                  sample=None,
                  pu=None,
                  tp=None,
                  tp_sel=None,
                  gen_sel=None):
        histo = None
        labels = []
        text = ''

        query = '(pu == @pu) & (tp == @tp) & (tp_sel == @tp_sel) & (classtype == @classtype)'
        if gen_sel is not None:
            query += ' & (gen_sel == @gen_sel)'
        else:
            query += ' & (gen_sel.isnull())'
        if sample is not None:
            query += '& (sample == @sample)'

        histo_df = self.data.query(query)

        if histo_df.empty:
            print 'No match found for: pu: {}, tp: {}, tp_sel: {}, gen_sel: {}, classtype: {}'.format(pu, tp, tp_sel, gen_sel, classtype)
            return None, None, None
#         print histo_df

        field_counts = histo_df.apply(lambda x: len(x.unique()))
        label_fields = []
        text_fields = []
        # print field_counts
        for field in field_counts.iteritems():
            if(field[1] > 1 and field[0] != 'histo'):
                label_fields.append(field[0])
            if(field[1] == 1 and field[0] != 'histo' and field[0] != 'classtype' and field[0] != 'sample'):
                if(gen_sel is None and field[0] == 'gen_sel'):
                    continue
                text_fields.append(field[0])
#         print 'label fields: {}'.format(label_fields)
#         print 'text fields: {}'.format(text_fields)

        for item in histo_df[label_fields].iterrows():
            labels.append(', '.join([self.labels_dict[tx] for tx in item[1].values if self.labels_dict[tx] != '']))

        # print labels
        text = ', '.join([self.labels_dict[fl] for fl in histo_df[text_fields].iloc[0].values if self.labels_dict[fl] != ''])
        histo = [his.get() for his in histo_df['histo'].values]
        return histo, labels, text


# -------------------------------------------------------------------------

samples_ele = [
    Sample('ele_flat2to100_PU0', 'PU0', version, 'ele'),
    Sample('ele_flat2to100_PU200', 'PU200', version, 'ele')
    ]

samples_photons = [
    Sample('photon_flat8to150_PU0', 'PU0', version, 'photon'),
    Sample('photon_flat8to150_PU200', 'PU200', version, 'photon')
    ]

samples_pions = [
    Sample('pion_flat2to100_PU0', 'PU0', version, 'pions'),
    ]

samples_nugus = [
    Sample('nugun_alleta_pu0', 'PU0', version, 'mb'),
    Sample('nugun_alleta_pu200', 'PU200', version, 'mb')
    ]

samples_nugunrates = [
    Sample('nugun_alleta_pu200', 'PU200', version, 'mb')
    ]

tpsets = {'DEF': 'NNDR',
          'DEFCalib': 'NNDR Calib v1',
          'DEFMerged': 'NNDR(merged)'}

tpset_selections = {}
gen_selections = {}
samples = []

# tpset_selections.update(get_label_dict(tp_rate_selections))
tpset_selections.update(get_label_dict(selections.tp_match_selections))
gen_selections.update(get_label_dict(selections.gen_part_selections))
gen_selections.update({'nomatch': ''})


gen_part_selections: 10


Error in <TFile::TFile>: file ../plots1/histos_pion_flat2to100_PU0_v61t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_nugun_alleta_pu0_v61t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_nugun_alleta_pu200_v61t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_nugun_alleta_pu200_v61t.root does not exist


In [5]:
%%time

hplot = HPlot(samples, tpsets, tpset_selections, gen_selections)
samples = samples_ele
samples.extend(samples_photons)

hplot.cache_histo(classtype=histos.HistoSetReso, 
                  samples=samples,
                  pus=[],
                  tps=tpsets,
                  tp_sels=tpset_selections,
                  gen_sels=gen_selections)



<__main__.Sample instance at 0x1209b8dd0>
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em GENPt40
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em GENEtaC
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em GENEtaB
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em GENEtaD
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em GENEtaBC
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em GENPt30
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em GENPt20
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em GENEtaBCD
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em GENPt10
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em nomatch
<__main__.Sample instance at 0x1209b8dd0> DEFMerged Em GEN
<__main__.Sample instance at 0x1209b8dd0> DEFMerged all GENPt40
<__main__.Sample instance at 0x1209b8dd0> DEFMerged all GENEtaC
<__main__.Sample instance at 0x1209b8dd0> DEFMerged all GENEtaB
<__main__.Sample instance at 0x1209b8dd0> DEFMerged all GENEtaD
<__main__.

<__main__.Sample instance at 0x1209b8dd0> DEFCalib EmPt20 GEN
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 GENPt40
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 GENEtaC
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 GENEtaB
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 GENEtaD
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 GENEtaBC
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 GENPt30
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 GENPt20
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 GENEtaBCD
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 GENPt10
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 nomatch
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt30 GEN
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt20 GENPt40
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt20 GENEtaC
<__main__.Sample instance at 0x1209b8dd0> DEFCalib Pt20 GENEtaB
<__main__.Sample instance at 0x1209b8dd0> D

<__main__.Sample instance at 0x1209c3950> DEFMerged Pt10 GENEtaB
<__main__.Sample instance at 0x1209c3950> DEFMerged Pt10 GENEtaD
<__main__.Sample instance at 0x1209c3950> DEFMerged Pt10 GENEtaBC
<__main__.Sample instance at 0x1209c3950> DEFMerged Pt10 GENPt30
<__main__.Sample instance at 0x1209c3950> DEFMerged Pt10 GENPt20
<__main__.Sample instance at 0x1209c3950> DEFMerged Pt10 GENEtaBCD
<__main__.Sample instance at 0x1209c3950> DEFMerged Pt10 GENPt10
<__main__.Sample instance at 0x1209c3950> DEFMerged Pt10 nomatch
<__main__.Sample instance at 0x1209c3950> DEFMerged Pt10 GEN
<__main__.Sample instance at 0x1209c3950> DEFMerged EmPt30 GENPt40
<__main__.Sample instance at 0x1209c3950> DEFMerged EmPt30 GENEtaC
<__main__.Sample instance at 0x1209c3950> DEFMerged EmPt30 GENEtaB
<__main__.Sample instance at 0x1209c3950> DEFMerged EmPt30 GENEtaD
<__main__.Sample instance at 0x1209c3950> DEFMerged EmPt30 GENEtaBC
<__main__.Sample instance at 0x1209c3950> DEFMerged EmPt30 GENPt30
<__main__.Sam

<__main__.Sample instance at 0x1209c3950> DEFCalib Pt30 GEN
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 GENPt40
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 GENEtaC
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 GENEtaB
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 GENEtaD
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 GENEtaBC
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 GENPt30
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 GENPt20
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 GENEtaBCD
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 GENPt10
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 nomatch
<__main__.Sample instance at 0x1209c3950> DEFCalib Pt20 GEN
<__main__.Sample instance at 0x1209c3950> DEFCalib EmPt10 GENPt40
<__main__.Sample instance at 0x1209c3950> DEFCalib EmPt10 GENEtaC
<__main__.Sample instance at 0x1209c3950> DEFCalib EmPt10 GENEtaB
<__main__.Sample instance at 0x1209c395

<__main__.Sample instance at 0x1209b8ea8> DEFMerged Pt10 GENEtaBCD
<__main__.Sample instance at 0x1209b8ea8> DEFMerged Pt10 GENPt10
<__main__.Sample instance at 0x1209b8ea8> DEFMerged Pt10 nomatch
<__main__.Sample instance at 0x1209b8ea8> DEFMerged Pt10 GEN
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 GENPt40
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 GENEtaC
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 GENEtaB
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 GENEtaD
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 GENEtaBC
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 GENPt30
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 GENPt20
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 GENEtaBCD
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 GENPt10
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 nomatch
<__main__.Sample instance at 0x1209b8ea8> DEFMerged EmPt30 GEN
<__mai

<__main__.Sample instance at 0x1209b8ea8> DEFCalib EmPt10 GENEtaC
<__main__.Sample instance at 0x1209b8ea8> DEFCalib EmPt10 GENEtaB
<__main__.Sample instance at 0x1209b8ea8> DEFCalib EmPt10 GENEtaD
<__main__.Sample instance at 0x1209b8ea8> DEFCalib EmPt10 GENEtaBC
<__main__.Sample instance at 0x1209b8ea8> DEFCalib EmPt10 GENPt30
<__main__.Sample instance at 0x1209b8ea8> DEFCalib EmPt10 GENPt20
<__main__.Sample instance at 0x1209b8ea8> DEFCalib EmPt10 GENEtaBCD
<__main__.Sample instance at 0x1209b8ea8> DEFCalib EmPt10 GENPt10
<__main__.Sample instance at 0x1209b8ea8> DEFCalib EmPt10 nomatch
<__main__.Sample instance at 0x1209b8ea8> DEFCalib EmPt10 GEN
<__main__.Sample instance at 0x1209b8ea8> DEF Em GENPt40
<__main__.Sample instance at 0x1209b8ea8> DEF Em GENEtaC
<__main__.Sample instance at 0x1209b8ea8> DEF Em GENEtaB
<__main__.Sample instance at 0x1209b8ea8> DEF Em GENEtaD
<__main__.Sample instance at 0x1209b8ea8> DEF Em GENEtaBC
<__main__.Sample instance at 0x1209b8ea8> DEF Em GENPt3

<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt30 GEN
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 GENPt40
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 GENEtaC
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 GENEtaB
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 GENEtaD
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 GENEtaBC
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 GENPt30
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 GENPt20
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 GENEtaBCD
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 GENPt10
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 nomatch
<__main__.Sample instance at 0x1209c39e0> DEFMerged EmPt20 GEN
<__main__.Sample instance at 0x1209c39e0> DEFMerged Pt30 GENPt40
<__main__.Sample instance at 0x1209c39e0> DEFMerged Pt30 GENEtaC
<__main__.Sample instance at 0x1209c39e0> DEFMerged Pt30 GENEtaB
<__mai

<__main__.Sample instance at 0x1209c39e0> DEF all GENEtaC
<__main__.Sample instance at 0x1209c39e0> DEF all GENEtaB
<__main__.Sample instance at 0x1209c39e0> DEF all GENEtaD
<__main__.Sample instance at 0x1209c39e0> DEF all GENEtaBC
<__main__.Sample instance at 0x1209c39e0> DEF all GENPt30
<__main__.Sample instance at 0x1209c39e0> DEF all GENPt20
<__main__.Sample instance at 0x1209c39e0> DEF all GENEtaBCD
<__main__.Sample instance at 0x1209c39e0> DEF all GENPt10
<__main__.Sample instance at 0x1209c39e0> DEF all nomatch
<__main__.Sample instance at 0x1209c39e0> DEF all GEN
<__main__.Sample instance at 0x1209c39e0> DEF Pt10 GENPt40
<__main__.Sample instance at 0x1209c39e0> DEF Pt10 GENEtaC
<__main__.Sample instance at 0x1209c39e0> DEF Pt10 GENEtaB
<__main__.Sample instance at 0x1209c39e0> DEF Pt10 GENEtaD
<__main__.Sample instance at 0x1209c39e0> DEF Pt10 GENEtaBC
<__main__.Sample instance at 0x1209c39e0> DEF Pt10 GENPt30
<__main__.Sample instance at 0x1209c39e0> DEF Pt10 GENPt20
<__main

In [6]:
hplot.data

sample     pu         tp  tp_sel    gen_sel  \
0        ele    PU0  DEFMerged      Em    GENPt40   
1        ele    PU0  DEFMerged      Em    GENEtaC   
2        ele    PU0  DEFMerged      Em    GENEtaB   
3        ele    PU0  DEFMerged      Em    GENEtaD   
4        ele    PU0  DEFMerged      Em   GENEtaBC   
5        ele    PU0  DEFMerged      Em    GENPt30   
6        ele    PU0  DEFMerged      Em    GENPt20   
7        ele    PU0  DEFMerged      Em  GENEtaBCD   
8        ele    PU0  DEFMerged      Em    GENPt10   
9        ele    PU0  DEFMerged      Em    nomatch   
10       ele    PU0  DEFMerged      Em        GEN   
11       ele    PU0  DEFMerged     all    GENPt40   
12       ele    PU0  DEFMerged     all    GENEtaC   
13       ele    PU0  DEFMerged     all    GENEtaB   
14       ele    PU0  DEFMerged     all    GENEtaD   
15       ele    PU0  DEFMerged     all   GENEtaBC   
16       ele    PU0  DEFMerged     all    GENPt30   
17       ele    PU0  DEFMerged     all    GENPt20   
18       ele    PU0  DEFMerged     all  GENEtaBCD   
19       ele    PU0  DEFMerged     all    GENPt10   
20       ele    PU0  DEFMerged     all    nomatch   
21       ele    PU0  DEFMerged     all        GEN   
22       ele    PU0  DEFMerged    Pt10    GENPt40   
23       ele    PU0  DEFMerged    Pt10    GENEtaC   
24       ele    PU0  DEFMerged    Pt10    GENEtaB   
25       ele    PU0  DEFMerged    Pt10    GENEtaD   
26       ele    PU0  DEFMerged    Pt10   GENEtaBC   
27       ele    PU0  DEFMerged    Pt10    GENPt30   
28       ele    PU0  DEFMerged    Pt10    GENPt20   
29       ele    PU0  DEFMerged    Pt10  GENEtaBCD   
...      ...    ...        ...     ...        ...   
1026  photon  PU200        DEF    Pt30    GENEtaD   
1027  photon  PU200        DEF    Pt30   GENEtaBC   
1028  photon  PU200        DEF    Pt30    GENPt30   
1029  photon  PU200        DEF    Pt30    GENPt20   
1030  photon  PU200        DEF    Pt30  GENEtaBCD   
1031  photon  PU200        DEF    Pt30    GENPt10   
1032  photon  PU200        DEF    Pt30    nomatch   
1033  photon  PU200        DEF    Pt30        GEN   
1034  photon  PU200        DEF    Pt20    GENPt40   
1035  photon  PU200        DEF    Pt20    GENEtaC   
1036  photon  PU200        DEF    Pt20    GENEtaB   
1037  photon  PU200        DEF    Pt20    GENEtaD   
1038  photon  PU200        DEF    Pt20   GENEtaBC   
1039  photon  PU200        DEF    Pt20    GENPt30   
1040  photon  PU200        DEF    Pt20    GENPt20   
1041  photon  PU200        DEF    Pt20  GENEtaBCD   
1042  photon  PU200        DEF    Pt20    GENPt10   
1043  photon  PU200        DEF    Pt20    nomatch   
1044  photon  PU200        DEF    Pt20        GEN   
1045  photon  PU200        DEF  EmPt10    GENPt40   
1046  photon  PU200        DEF  EmPt10    GENEtaC   
1047  photon  PU200        DEF  EmPt10    GENEtaB   
1048  photon  PU200        DEF  EmPt10    GENEtaD   
1049  photon  PU200        DEF  EmPt10   GENEtaBC   
1050  photon  PU200        DEF  EmPt10    GENPt30   
1051  photon  PU200        DEF  EmPt10    GENPt20   
1052  photon  PU200        DEF  EmPt10  GENEtaBCD   
1053  photon  PU200        DEF  EmPt10    GENPt10   
1054  photon  PU200        DEF  EmPt10    nomatch   
1055  photon  PU200        DEF  EmPt10        GEN   

                          classtype                                      histo  
0     python.l1THistos.HistoSetReso  <__main__.HProxy instance at 0x11fe46908>  
1     python.l1THistos.HistoSetReso  <__main__.HProxy instance at 0x12095fea8>  
2     python.l1THistos.HistoSetReso  <__main__.HProxy instance at 0x10f731878>  
3     python.l1THistos.HistoSetReso  <__main__.HProxy instance at 0x10fa64908>  
4     python.l1THistos.HistoSetReso  <__main__.HProxy instance at 0x12095ffc8>  
5     python.l1THistos.HistoSetReso  <__main__.HProxy instance at 0x12095fb48>  
6     python.l1THistos.HistoSetReso  <__main__.HProxy instance at 0x12098bf80>  
7     python.l1THistos.HistoSetReso  <__main__.HProxy instance at 0x120

In [7]:
# dir(histo_reso_df.loc['DEF', 'ele'][0])
tps = ['DEF', 'DEFMerged']
tp_select = ['Em']
gen_select = ['GENEtaBC', 'GENEtaBCD']


## $p_{T}$ response

### electrons

In [8]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in gen_select:
            hsets, labels, text = hplot.get_histo(histos.HistoSetReso, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            print tp, tp_sel, gen_sel
            draw([his.hreso.h_ptResp for his in hsets], labels, norm=True, text=text, v_lines=[1.0])


DEF Em GENEtaBC
DEF Em GENEtaBCD
DEFMerged Em GENEtaBC
DEFMerged Em GENEtaBCD


### photons

In [9]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in gen_select:
            hsets, labels, text = hplot.get_histo(histos.HistoSetReso, 'photon', ['PU0', 'PU200'], tp, tp_sel, gen_sel)            
            print tp, tp_sel, gen_sel
            draw([his.hreso.h_ptResp for his in hsets], labels, norm=True, text=text, v_lines=[1.0])


DEF Em GENEtaBC
DEF Em GENEtaBCD
DEFMerged Em GENEtaBC
DEFMerged Em GENEtaBCD


## Derive calibrations

In [10]:
def gaussfit(project_hist):
    max_bin = project_hist.GetMaximumBin()
    max_value = project_hist.GetBinCenter(max_bin)
    rms_value = project_hist.GetRMS()
    
    k_l = 0.5
    k_r = 1.
#         if(gen_sel) == 'eleD':
#             k_l = 1.5
#             k_r = 2.
    print '   max_value = {}, RMS = {}'.format(max_value, rms_value)
    result = project_hist.Fit('gaus','QERLS+', '', max_value-k_l*rms_value,  max_value+k_r*rms_value)
    # result.Print()
    print '   mean = {}, sigma = {}'.format(result.GetParams()[1], result.GetParams()[2])
    func = project_hist.GetFunction("gaus")
    print '   NDF = {}, chi2 = {}, prob = {}'.format(func.GetNDF(), func.GetChisquare(), func.GetProb())
    return result 


def gausstailfit(project_hist):
    max_bin = project_hist.GetMaximumBin()
    max_value = project_hist.GetBinCenter(max_bin)
    rms_value = project_hist.GetRMS()

    def gausstail(x, p):
        #         // [Constant] * ROOT::Math::crystalball_function(x, [Alpha], [N], [Sigma], [Mean])
        return p[0] * ROOT.Math.crystalball_function(x[0], p[3], p[4], p[2], p[1])

    fitf = ROOT.TF1('gausstail', gausstail, 0, 3, 5)
    fitf.SetParNames('norm', 'mean', 'sigma', 'alpha', 'n')
#     fitf.FixParameter(0, 1.)
    fitf.SetParLimits(1, 0.8, 1.1)

    fitf.SetParameters(project_hist.Integral(),max_value,rms_value, 1, 1)
#     c = newCanvas()
#     fitf.Draw()
#     c.Draw()
    # print '   max_value = {}, RMS = {}'.format(max_value, rms_value)
    result = project_hist.Fit('gausstail','NQERLS+')
    # result.Print()
    # print '   mean = {}, sigma = {}'.format(result.GetParams()[1], result.GetParams()[2])
#     func = project_hist.GetFunction("gaus")
    # print '   NDF = {}, chi2 = {}, prob = {}'.format(fitf.GetNDF(), fitf.GetChisquare(), fitf.GetProb())
    return result


### electrons

#### STD clusters

In [11]:
calib_reco_df = pd.DataFrame(columns=['samp_type', 'tp', 'eta_l', 'eta_h', 'pt_l', 'pt_h', 'peak', 'avg', 'mdn'])



In [12]:
from array import array

In [13]:
tp_set = 'DEF'
sample = 'ele'

hsets, labels, text = hplot.get_histo(histos.HistoSetReso, sample, ['PU0', 'PU200'], tp_set, 'Em', 'GEN') 
hByTPset = [his.hreso.h_ptRespVetaVptL1 for his in hsets]
draw(hByTPset, labels=labels, text=text, options='COLZ')
histo_3d = hByTPset[0]
#         for eta_range in [(7,7), (8,11), (12, 14)]:
for eta_range in [(7,7), (8,9), (10,11), (12, 14), (15,18)]:
    eta_range_values = (histo_3d.GetXaxis().GetBinLowEdge(eta_range[0]), histo_3d.GetXaxis().GetBinUpEdge(eta_range[1]))
    # for pt_range in [(3,5), (6,10), (11,15), (16,20), (21,50)]:
    for pt_range in [(3,5), (6,7), (8,9), (10,11), (12,13), (14,15), (16,17), (18,19), (20,21), (22,50)]:
        pt_range_values = (histo_3d.GetYaxis().GetBinLowEdge(pt_range[0]), histo_3d.GetYaxis().GetBinUpEdge(pt_range[1]))
        print 'eta range: from eta {} (bin {}) to eta {} (bin {})'.format(eta_range_values[0], eta_range[0], eta_range_values[1], eta_range[1])
        print 'pt range: from pt {} [GeV] (bin {}) to pt {} [GeV] (bin {})'.format(pt_range_values[0], pt_range[0], pt_range_values[1], pt_range[1])
        hname = 'pt{}to{}_eta{}to{}'.format(pt_range_values[0], pt_range_values[1], eta_range_values[0], eta_range_values[1])
        respPlot = histo_3d.ProjectionZ(hname, eta_range[0], eta_range[1], pt_range[0], pt_range[1], '')
        respPlot.GetXaxis().SetRangeUser(0.7, 1.5)
        max_bin = respPlot.GetMaximumBin()
        max_value = respPlot.GetBinCenter(max_bin)
        rms_value = respPlot.GetRMS()
        respPlot.GetXaxis().SetRangeUser(0, 3)
        print '   max_value = {}, RMS = {}'.format(max_value, rms_value)
        quantile = array('d', [1])
        respPlot.GetQuantiles(1, quantile, array('d', [0.5]))

        k_l = 0.5
        k_r = 1.
        if pt_range_values[0] > 30 or eta_range[0] > 14:
            k_l = 1.
        #fitf = ROOT.TF1('myfunc', 'gaus')
        #fitf.SetParameter(0,0.93)
        draw([respPlot], labels=['PU0'], text=hname)

        result = respPlot.Fit('gaus','QERLS+', '', max_value-k_l*rms_value,  max_value+k_r*rms_value)
        result.Print()
        print '   mean = {}, sigma= {}'.format(result.GetParams()[1], result.GetParams()[2],)

        calib_reco_df= calib_reco_df.append({'samp_type': sample,
                                             'tp': tp_set,
                                             'eta_l': eta_range_values[0], 
                                             'eta_h': eta_range_values[1], 
                                             'pt_l': pt_range_values[0],
                                             'pt_h': pt_range_values[1],
                                             'peak': result.GetParams()[1],
                                             'avg': respPlot.GetMean(),
                                             'mdn': quantile[0]}, ignore_index=True)
        ROOT.gStyle.SetOptFit(11111)


eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 4.0 [GeV] (bin 3) to pt 10.0 [GeV] (bin 5)
   max_value = 0.885, RMS = 0.0847643589004
   mean = 0.8742459956, sigma= 0.0458465684539
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 10.0 [GeV] (bin 6) to pt 14.0 [GeV] (bin 7)
   max_value = 0.735, RMS = 0.0969372847003
   mean = 0.949341827954, sigma= 0.427698084726
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 14.0 [GeV] (bin 8) to pt 18.0 [GeV] (bin 9)
   max_value = 0.855, RMS = 0.0937476963263
   mean = 0.889335051085, sigma= 0.129152296164
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 18.0 [GeV] (bin 10) to pt 22.0 [GeV] (bin 11)
   max_value = 0.885, RMS = 0.0969459918169
   mean = 0.891401913153, sigma= 0.12808520094
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 22.0 [GeV] (bin 12) to pt 26.0 [GeV] (bin 13)
   max_value = 0.885, RMS = 0.0923146551505
   mean = 0.9257283559

In [14]:
calib_reco_df[(calib_reco_df.samp_type == sample) & (calib_reco_df.tp == tp_set)]

samp_type   tp  eta_l  eta_h  pt_l   pt_h      peak       avg       mdn
0        ele  DEF    1.6    1.7   4.0   10.0  0.874246  0.604135  0.587500
1        ele  DEF    1.6    1.7  10.0   14.0  0.949342  0.706940  0.710000
2        ele  DEF    1.6    1.7  14.0   18.0  0.889335  0.765524  0.795000
3        ele  DEF    1.6    1.7  18.0   22.0  0.891402  0.792782  0.822375
4        ele  DEF    1.6    1.7  22.0   26.0  0.925728  0.810685  0.849667
5        ele  DEF    1.6    1.7  26.0   30.0  0.969569  0.830596  0.875385
6        ele  DEF    1.6    1.7  30.0   34.0  0.944110  0.852172  0.886579
7        ele  DEF    1.6    1.7  34.0   38.0  0.959291  0.880986  0.918358
8        ele  DEF    1.6    1.7  38.0   42.0  0.940722  0.879595  0.907131
9        ele  DEF    1.6    1.7  42.0  100.0  0.966775  0.929160  0.947597
10       ele  DEF    1.7    1.9   4.0   10.0  0.838173  0.633615  0.625068
11       ele  DEF    1.7    1.9  10.0   14.0  0.886127  0.740071  0.765923
12       ele  DEF    1.7    1.9  14.0   18.0  0.910046  0.782302  0.818961
13       ele  DEF    1.7    1.9  18.0   22.0  0.942080  0.823326  0.856807
14       ele  DEF    1.7    1.9  22.0   26.0  0.940121  0.854863  0.891117
15       ele  DEF    1.7    1.9  26.0   30.0  0.946097  0.870872  0.900104
16       ele  DEF    1.7    1.9  30.0   34.0  0.947096  0.877643  0.905856
17       ele  DEF    1.7    1.9  34.0   38.0  0.944052  0.891393  0.915189
18       ele  DEF    1.7    1.9  38.0   42.0  0.941594  0.891381  0.913597
19       ele  DEF    1.7    1.9  42.0  100.0  0.960563  0.929001  0.943828
20       ele  DEF    1.9    2.1   4.0   10.0  0.867935  0.695131  0.714041
21       ele  DEF    1.9    2.1  10.0   14.0  0.899810  0.793677  0.833833
22       ele  DEF    1.9    2.1  14.0   18.0  0.919026  0.835893  0.869459
23       ele  DEF    1.9    2.1  18.0   22.0  0.931893  0.865131  0.896875
24       ele  DEF    1.9    2.1  22.0   26.0  0.938326  0.880905  0.900882
25       ele  DEF    1.9    2.1  26.0   30.0  0.941808  0.889307  0.911729
26       ele  DEF    1.9    2.1  30.0   34.0  0.941817  0.900408  0.920455
27       ele  DEF    1.9    2.1  34.0   38.0  0.939094  0.903840  0.920911
28       ele  DEF    1.9    2.1  38.0   42.0  0.940724  0.906181  0.923408
29       ele  DEF    1.9    2.1  42.0  100.0  0.957682  0.933514  0.945974
30       ele  DEF    2.1    2.4   4.0   10.0  0.875397  0.759130  0.795000
31       ele  DEF    2.1    2.4  10.0   14.0  0.905521  0.835351  0.863242
32       ele  DEF    2.1    2.4  14.0   18.0  0.913860  0.866997  0.885750
33       ele  DEF    2.1    2.4  18.0   22.0  0.919893  0.883848  0.902934
34       ele  DEF    2.1    2.4  22.0   26.0  0.923964  0.893834  0.909146
35       ele  DEF    2.1    2.4  26.0   30.0  0.934802  0.904840  0.917923
36       ele  DEF    2.1    2.4  30.0   34.0  0.939052  0.911179  0.924167
37       ele  DEF    2.1    2.4  34.0   38.0  0.936018  0.912699  0.925909
38       ele  DEF    2.1    2.4  38.0   42.0  0.939864  0.917594  0.932430
39       ele  DEF    2.1    2.4  42.0  100.0  0.960475  0.937664  0.947653
40       ele  DEF    2.4    2.8   4.0   10.0  0.859137  0.823810  0.842552
41       ele  DEF    2.4    2.8  10.0   14.0  0.886328  0.873857  0.882811
42       ele  DEF    2.4    2.8  14.0   18.0  0.906907  0.891475  0.900514
43       ele  DEF    2.4    2.8  18.0   22.0  0.918338  0.904919  0.912419
44       ele  DEF    2.4    2.8  22.0   26.0  0.928720  0.910986  0.918840
45       ele  DEF    2.4    2.8  26.0   30.0  0.930870  0.918043  0.925478
46       ele  DEF    2.4    2.8  30.0   34.0  0.935776  0.920989  0.929404
47       ele  DEF    2.4    2.8  34.0   38.0  0.941592  0.924681  0.933951
48       ele  DEF    2.4    2.8  38.0   42.0  0.942572  0.926921  0.935808
49       ele  DEF    2.4    2.8  42.0  100.0  0.958252  0.940277  0.948776

#### Merged 

In [15]:
tp_set = 'DEFMerged'
sample = 'ele'

hsets, labels, text = hplot.get_histo(histos.HistoSetReso, sample, ['PU0', 'PU200'], tp_set, 'Em', 'GEN') 
hByTPset = [his.hreso.h_ptRespVetaVptL1 for his in hsets]
draw(hByTPset, labels=labels, text=text, options='COLZ')
histo_3d = hByTPset[0]
#         for eta_range in [(7,7), (8,11), (12, 14)]:
for eta_range in [(7,7), (8,9), (10,11), (12, 14), (15,18)]:
    eta_range_values = (histo_3d.GetXaxis().GetBinLowEdge(eta_range[0]), histo_3d.GetXaxis().GetBinUpEdge(eta_range[1]))
    # for pt_range in [(3,5), (6,10), (11,15), (16,20), (21,50)]:
    for pt_range in [(3,5), (6,7), (8,9), (10,11), (12,13), (14,15), (16,17), (18,19), (20,21), (22,50)]:
        pt_range_values = (histo_3d.GetYaxis().GetBinLowEdge(pt_range[0]), histo_3d.GetYaxis().GetBinUpEdge(pt_range[1]))
        print 'eta range: from eta {} (bin {}) to eta {} (bin {})'.format(eta_range_values[0], eta_range[0], eta_range_values[1], eta_range[1])
        print 'pt range: from pt {} [GeV] (bin {}) to pt {} [GeV] (bin {})'.format(pt_range_values[0], pt_range[0], pt_range_values[1], pt_range[1])
        hname = 'pt{}to{}_eta{}to{}'.format(pt_range_values[0], pt_range_values[1], eta_range_values[0], eta_range_values[1])
        respPlot = histo_3d.ProjectionZ(hname, eta_range[0], eta_range[1], pt_range[0], pt_range[1], '')
        respPlot.GetXaxis().SetRangeUser(0.7, 1.5)
        max_bin = respPlot.GetMaximumBin()
        max_value = respPlot.GetBinCenter(max_bin)
        rms_value = respPlot.GetRMS()
        respPlot.GetXaxis().SetRangeUser(0, 3)
        print '   max_value = {}, RMS = {}'.format(max_value, rms_value)
        quantile = array('d', [1])
        respPlot.GetQuantiles(1, quantile, array('d', [0.5]))

        k_l = 0.5
        k_r = 1.
        if pt_range_values[0] > 30 or eta_range[0] > 14:
            k_l = 1.
        #fitf = ROOT.TF1('myfunc', 'gaus')
        #fitf.SetParameter(0,0.93)
        draw([respPlot], labels=['PU0'], text=hname)

        result = respPlot.Fit('gaus','QERLS+', '', max_value-k_l*rms_value,  max_value+k_r*rms_value)
        result.Print()
        print '   mean = {}, sigma= {}'.format(result.GetParams()[1], result.GetParams()[2],)

        calib_reco_df= calib_reco_df.append({'samp_type': sample,
                                             'tp': tp_set,
                                             'eta_l': eta_range_values[0], 
                                             'eta_h': eta_range_values[1], 
                                             'pt_l': pt_range_values[0],
                                             'pt_h': pt_range_values[1],
                                             'peak': result.GetParams()[1],
                                             'avg': respPlot.GetMean(),
                                             'mdn': quantile[0]}, ignore_index=True)
        ROOT.gStyle.SetOptFit(11111)



eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 4.0 [GeV] (bin 3) to pt 10.0 [GeV] (bin 5)
   max_value = 0.765, RMS = 0.082734792865
   mean = 0.788845589161, sigma= 0.0740879804532
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 10.0 [GeV] (bin 6) to pt 14.0 [GeV] (bin 7)
   max_value = 0.855, RMS = 0.0936829824554
   mean = 0.843294779329, sigma= 0.125774694562
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 14.0 [GeV] (bin 8) to pt 18.0 [GeV] (bin 9)
   max_value = 0.855, RMS = 0.0897058283127
   mean = 0.878480669143, sigma= 0.0902769869191
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 18.0 [GeV] (bin 10) to pt 22.0 [GeV] (bin 11)
   max_value = 0.915, RMS = 0.0912520173067
   mean = 0.893479720513, sigma= 0.0935500181557
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 22.0 [GeV] (bin 12) to pt 26.0 [GeV] (bin 13)
   max_value = 0.885, RMS = 0.086925931637
   mean = 0.9348176


****************************************
Minimizer is Minuit / Migrad
MinFCN                    =     0.628153
Chi2                      =      1.26813
NDf                       =            1
Edm                       =  1.88281e-08
NCalls                    =          126
Constant                  =      34.4277   +/-   4.6378      
Mean                      =     0.788846   +/-   0.0177049   
Sigma                     =     0.074088   +/-   0.0401332    	 (limited)

****************************************
Minimizer is Minuit / Migrad
MinFCN                    =     0.253566
Chi2                      =     0.521661
NDf                       =            2
Edm                       =  2.77655e-06
NCalls                    =          147
Constant                  =      43.9726   +/-   4.20608     
Mean                      =     0.843295   +/-   0.0662109   
Sigma                     =     0.125775   +/-   0.0910713    	 (limited)

****************************************
Minimizer 

In [16]:
calib_reco_df[(calib_reco_df.samp_type == sample) & (calib_reco_df.tp == tp_set)]

samp_type         tp  eta_l  eta_h  pt_l   pt_h      peak       avg  \
50       ele  DEFMerged    1.6    1.7   4.0   10.0  0.788846  0.643777   
51       ele  DEFMerged    1.6    1.7  10.0   14.0  0.843295  0.768964   
52       ele  DEFMerged    1.6    1.7  14.0   18.0  0.878481  0.832877   
53       ele  DEFMerged    1.6    1.7  18.0   22.0  0.893480  0.846961   
54       ele  DEFMerged    1.6    1.7  22.0   26.0  0.934818  0.861489   
55       ele  DEFMerged    1.6    1.7  26.0   30.0  0.950601  0.877426   
56       ele  DEFMerged    1.6    1.7  30.0   34.0  0.947824  0.889181   
57       ele  DEFMerged    1.6    1.7  34.0   38.0  0.955768  0.908045   
58       ele  DEFMerged    1.6    1.7  38.0   42.0  0.941561  0.904363   
59       ele  DEFMerged    1.6    1.7  42.0  100.0  0.965988  0.937657   
60       ele  DEFMerged    1.7    1.9   4.0   10.0  0.828484  0.673391   
61       ele  DEFMerged    1.7    1.9  10.0   14.0  0.837601  0.784831   
62       ele  DEFMerged    1.7    1.9  14.0   18.0  0.904420  0.822587   
63       ele  DEFMerged    1.7    1.9  18.0   22.0  0.929212  0.856610   
64       ele  DEFMerged    1.7    1.9  22.0   26.0  0.937863  0.877166   
65       ele  DEFMerged    1.7    1.9  26.0   30.0  0.943276  0.888955   
66       ele  DEFMerged    1.7    1.9  30.0   34.0  0.945069  0.895167   
67       ele  DEFMerged    1.7    1.9  34.0   38.0  0.941094  0.906921   
68       ele  DEFMerged    1.7    1.9  38.0   42.0  0.942377  0.902959   
69       ele  DEFMerged    1.7    1.9  42.0  100.0  0.960578  0.934205   
70       ele  DEFMerged    1.9    2.1   4.0   10.0  0.843465  0.720819   
71       ele  DEFMerged    1.9    2.1  10.0   14.0  0.901609  0.822186   
72       ele  DEFMerged    1.9    2.1  14.0   18.0  0.919041  0.854121   
73       ele  DEFMerged    1.9    2.1  18.0   22.0  0.930023  0.877031   
74       ele  DEFMerged    1.9    2.1  22.0   26.0  0.937245  0.890911   
75       ele  DEFMerged    1.9    2.1  26.0   30.0  0.941020  0.900378   
76       ele  DEFMerged    1.9    2.1  30.0   34.0  0.941407  0.905773   
77       ele  DEFMerged    1.9    2.1  34.0   38.0  0.937932  0.908793   
78       ele  DEFMerged    1.9    2.1  38.0   42.0  0.939972  0.911835   
79       ele  DEFMerged    1.9    2.1  42.0  100.0  0.957523  0.935360   
80       ele  DEFMerged    2.1    2.4   4.0   10.0  0.874472  0.772915   
81       ele  DEFMerged    2.1    2.4  10.0   14.0  0.905081  0.844860   
82       ele  DEFMerged    2.1    2.4  14.0   18.0  0.912401  0.872249   
83       ele  DEFMerged    2.1    2.4  18.0   22.0  0.919568  0.888082   
84       ele  DEFMerged    2.1    2.4  22.0   26.0  0.923327  0.897531   
85       ele  DEFMerged    2.1    2.4  26.0   30.0  0.934426  0.906931   
86       ele  DEFMerged    2.1    2.4  30.0   34.0  0.938871  0.913609   
87       ele  DEFMerged    2.1    2.4  34.0   38.0  0.935657  0.915195   
88       ele  DEFMerged    2.1    2.4  38.0   42.0  0.939717  0.920215   
89       ele  DEFMerged    2.1    2.4  42.0  100.0  0.960551  0.938120   
90       ele  DEFMerged    2.4    2.8   4.0   10.0  0.858716  0.826770   
91       ele  DEFMerged    2.4    2.8  10.0   14.0  0.886428  0.875854   
92       ele  DEFMerged    2.4    2.8  14.0   18.0  0.907122  0.892154   
93       ele  DEFMerged    2.4    2.8  18.0   22.0  0.918317  0.905868   
94       ele  DEFMerged    2.4    2.8  22.0   26.0  0.928356  0.911304   
95       ele  DEFMerged    2.4    2.8  26.0   30.0  0.930798  0.918941   
96       ele  DEFMerged    2.4    2.8  30.0   34.0  0.935799  0.921181   
97       ele  DEFMerged    2.4    2.8  34.0   38.0  0.941474  0.925105   
98       ele  DEFMerged    2.4    2.8  38.0   42.0  0.942699  0.927230   
99       ele  DEFMerged    2.4    2.8  42.0  100.0  0.958281  0.940384   

         mdn  
50  0.660469  
51  0.794651  
52  0.853125  
53  0.871667  
54  0.884589  
55  0.906908  
56  0.912500  
57  0.929241  
58  0.920179  
59  0.951579  
60  0.692037  
61  0.816262  
62  0.849153  
63  0.880697  
64 

### photons

#### STD clusters

In [17]:
tp_set = 'DEF'
sample = 'photon'

hsets, labels, text = hplot.get_histo(histos.HistoSetReso, sample, ['PU0', 'PU200'], tp_set, 'Em', 'GEN') 
hByTPset = [his.hreso.h_ptRespVetaVptL1 for his in hsets]
draw(hByTPset, labels=labels, text=text, options='COLZ')
histo_3d = hByTPset[0]
#         for eta_range in [(7,7), (8,11), (12, 14)]:
for eta_range in [(7,7), (8,9), (10,11), (12, 14), (15,18)]:
    eta_range_values = (histo_3d.GetXaxis().GetBinLowEdge(eta_range[0]), histo_3d.GetXaxis().GetBinUpEdge(eta_range[1]))
    # for pt_range in [(3,5), (6,10), (11,15), (16,20), (21,50)]:
    for pt_range in [(3,5), (6,7), (8,9), (10,11), (12,13), (14,15), (16,17), (18,19), (20,21), (22,50)]:
        pt_range_values = (histo_3d.GetYaxis().GetBinLowEdge(pt_range[0]), histo_3d.GetYaxis().GetBinUpEdge(pt_range[1]))
        print 'eta range: from eta {} (bin {}) to eta {} (bin {})'.format(eta_range_values[0], eta_range[0], eta_range_values[1], eta_range[1])
        print 'pt range: from pt {} [GeV] (bin {}) to pt {} [GeV] (bin {})'.format(pt_range_values[0], pt_range[0], pt_range_values[1], pt_range[1])
        hname = 'pt{}to{}_eta{}to{}'.format(pt_range_values[0], pt_range_values[1], eta_range_values[0], eta_range_values[1])
        respPlot = histo_3d.ProjectionZ(hname, eta_range[0], eta_range[1], pt_range[0], pt_range[1], '')
        respPlot.GetXaxis().SetRangeUser(0.7, 1.5)
        max_bin = respPlot.GetMaximumBin()
        max_value = respPlot.GetBinCenter(max_bin)
        rms_value = respPlot.GetRMS()
        respPlot.GetXaxis().SetRangeUser(0, 3)
        print '   max_value = {}, RMS = {}'.format(max_value, rms_value)
        quantile = array('d', [1])
        respPlot.GetQuantiles(1, quantile, array('d', [0.5]))

        k_l = 0.5
        k_r = 1.
        if pt_range_values[0] > 30 or eta_range[0] > 14:
            k_l = 1.
        #fitf = ROOT.TF1('myfunc', 'gaus')
        #fitf.SetParameter(0,0.93)
        draw([respPlot], labels=['PU0'], text=hname)

        result = respPlot.Fit('gaus','QERLS+', '', max_value-k_l*rms_value,  max_value+k_r*rms_value)
        result.Print()
        print '   mean = {}, sigma= {}'.format(result.GetParams()[1], result.GetParams()[2],)

        calib_reco_df= calib_reco_df.append({'samp_type': sample,
                                             'tp': tp_set,
                                             'eta_l': eta_range_values[0], 
                                             'eta_h': eta_range_values[1], 
                                             'pt_l': pt_range_values[0],
                                             'pt_h': pt_range_values[1],
                                             'peak': result.GetParams()[1],
                                             'avg': respPlot.GetMean(),
                                             'mdn': quantile[0]}, ignore_index=True)
        ROOT.gStyle.SetOptFit(11111)

eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 4.0 [GeV] (bin 3) to pt 10.0 [GeV] (bin 5)
   max_value = 0.885, RMS = 0.0543061688096
   mean = 0.896627693941, sigma= 0.0157968132581
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 10.0 [GeV] (bin 6) to pt 14.0 [GeV] (bin 7)
   max_value = 0.945, RMS = 0.0682880850795
   mean = 0.954614390384, sigma= 0.0314700517211
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 14.0 [GeV] (bin 8) to pt 18.0 [GeV] (bin 9)
   max_value = 0.915, RMS = 0.0582547836328
   mean = 0.927505250127, sigma= 0.0161300143967
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 18.0 [GeV] (bin 10) to pt 22.0 [GeV] (bin 11)
   max_value = 0.945, RMS = 0.0540486253496
   mean = 0.959404291626, sigma= 0.0166391045118
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 22.0 [GeV] (bin 12) to pt 26.0 [GeV] (bin 13)
   max_value = 0.945, RMS = 0.055953618109
   mean = 0.95791

eta range: from eta 2.4 (bin 15) to eta 2.8 (bin 18)
pt range: from pt 10.0 [GeV] (bin 6) to pt 14.0 [GeV] (bin 7)
   max_value = 0.915, RMS = 0.0435764844842
   mean = 0.908943473213, sigma= 0.0430824710141
eta range: from eta 2.4 (bin 15) to eta 2.8 (bin 18)
pt range: from pt 14.0 [GeV] (bin 8) to pt 18.0 [GeV] (bin 9)
   max_value = 0.915, RMS = 0.0434229045773
   mean = 0.917771037505, sigma= 0.040549463626
eta range: from eta 2.4 (bin 15) to eta 2.8 (bin 18)
pt range: from pt 18.0 [GeV] (bin 10) to pt 22.0 [GeV] (bin 11)
   max_value = 0.945, RMS = 0.0405623031011
   mean = 0.932536808881, sigma= 0.040163688427
eta range: from eta 2.4 (bin 15) to eta 2.8 (bin 18)
pt range: from pt 22.0 [GeV] (bin 12) to pt 26.0 [GeV] (bin 13)
   max_value = 0.945, RMS = 0.0432255129898
   mean = 0.933776968668, sigma= 0.0271100577982
eta range: from eta 2.4 (bin 15) to eta 2.8 (bin 18)
pt range: from pt 26.0 [GeV] (bin 14) to pt 30.0 [GeV] (bin 15)
   max_value = 0.945, RMS = 0.0432494296663
   me

In [18]:
calib_reco_df[(calib_reco_df.samp_type == sample) & (calib_reco_df.tp == tp_set)]

samp_type   tp  eta_l  eta_h  pt_l   pt_h      peak       avg       mdn
100    photon  DEF    1.6    1.7   4.0   10.0  0.896628  0.900405  0.898333
101    photon  DEF    1.6    1.7  10.0   14.0  0.954614  0.934180  0.943235
102    photon  DEF    1.6    1.7  14.0   18.0  0.927505  0.956507  0.951250
103    photon  DEF    1.6    1.7  18.0   22.0  0.959404  0.961935  0.962000
104    photon  DEF    1.6    1.7  22.0   26.0  0.957915  0.945423  0.948158
105    photon  DEF    1.6    1.7  26.0   30.0  0.959201  0.956020  0.958750
106    photon  DEF    1.6    1.7  30.0   34.0  0.942191  0.942541  0.946500
107    photon  DEF    1.6    1.7  34.0   38.0  0.976623  0.965625  0.971053
108    photon  DEF    1.6    1.7  38.0   42.0  0.972294  0.964138  0.969474
109    photon  DEF    1.6    1.7  42.0  100.0  0.983894  0.958546  0.970662
110    photon  DEF    1.7    1.9   4.0   10.0  0.933586  0.929423  0.932500
111    photon  DEF    1.7    1.9  10.0   14.0  0.928864  0.938571  0.935769
112    photon  DEF    1.7    1.9  14.0   18.0  0.959650  0.941640  0.941667
113    photon  DEF    1.7    1.9  18.0   22.0  0.956283  0.939733  0.942805
114    photon  DEF    1.7    1.9  22.0   26.0  0.956235  0.948699  0.948889
115    photon  DEF    1.7    1.9  26.0   30.0  0.982847  0.952573  0.958448
116    photon  DEF    1.7    1.9  30.0   34.0  0.959177  0.952615  0.957429
117    photon  DEF    1.7    1.9  34.0   38.0  0.954185  0.947571  0.954324
118    photon  DEF    1.7    1.9  38.0   42.0  0.972190  0.957941  0.966176
119    photon  DEF    1.7    1.9  42.0  100.0  0.970978  0.948267  0.962649
120    photon  DEF    1.9    2.1   4.0   10.0  0.928292  0.917842  0.917609
121    photon  DEF    1.9    2.1  10.0   14.0  0.927368  0.924362  0.922500
122    photon  DEF    1.9    2.1  14.0   18.0  0.956871  0.927821  0.930517
123    photon  DEF    1.9    2.1  18.0   22.0  0.959714  0.946875  0.950909
124    photon  DEF    1.9    2.1  22.0   26.0  0.959745  0.938130  0.945811
125    photon  DEF    1.9    2.1  26.0   30.0  0.957938  0.940066  0.946250
126    photon  DEF    1.9    2.1  30.0   34.0  0.957368  0.940537  0.943816
127    photon  DEF    1.9    2.1  34.0   38.0  0.969502  0.942273  0.960000
128    photon  DEF    1.9    2.1  38.0   42.0  0.962756  0.942310  0.950676
129    photon  DEF    1.9    2.1  42.0  100.0  0.970986  0.950333  0.962334
130    photon  DEF    2.1    2.4   4.0   10.0  0.925038  0.890702  0.898125
131    photon  DEF    2.1    2.4  10.0   14.0  0.899548  0.913916  0.910500
132    photon  DEF    2.1    2.4  14.0   18.0  0.925885  0.919565  0.916935
133    photon  DEF    2.1    2.4  18.0   22.0  0.929056  0.933670  0.935217
134    photon  DEF    2.1    2.4  22.0   26.0  0.958244  0.939328  0.942589
135    photon  DEF    2.1    2.4  26.0   30.0  0.958226  0.939089  0.945984
136    photon  DEF    2.1    2.4  30.0   34.0  0.955191  0.943585  0.946329
137    photon  DEF    2.1    2.4  34.0   38.0  0.960994  0.939653  0.945577
138    photon  DEF    2.1    2.4  38.0   42.0  0.954799  0.942789  0.948333
139    photon  DEF    2.1    2.4  42.0  100.0  0.964653  0.945151  0.956003
140    photon  DEF    2.4    2.8   4.0   10.0  0.881816  0.877562  0.880135
141    photon  DEF    2.4    2.8  10.0   14.0  0.908943  0.899700  0.901154
142    photon  DEF    2.4    2.8  14.0   18.0  0.917771  0.913761  0.916615
143    photon  DEF    2.4    2.8  18.0   22.0  0.932537  0.924000  0.928065
144    photon  DEF    2.4    2.8  22.0   26.0  0.933777  0.922282  0.928500
145    photon  DEF    2.4    2.8  26.0   30.0  0.931201  0.928028  0.930562
146    photon  DEF    2.4    2.8  30.0   34.0  0.932739  0.935000  0.935926
147    photon  DEF    2.4    2.8  34.0   38.0  0.946771  0.935280  0.941753
148    photon  DEF    2.4    2.8  38.0   42.0  0.951102  0.934518  0.944850
149    photon  DEF    2.4    2.8  42.0  100.0  0.962037  0.941980  0.952095

#### Merged

In [19]:
tp_set = 'DEFMerged'
sample = 'photon'

hsets, labels, text = hplot.get_histo(histos.HistoSetReso, sample, ['PU0', 'PU200'], tp_set, 'Em', 'GEN') 
hByTPset = [his.hreso.h_ptRespVetaVptL1 for his in hsets]
draw(hByTPset, labels=labels, text=text, options='COLZ')
histo_3d = hByTPset[0]
#         for eta_range in [(7,7), (8,11), (12, 14)]:
for eta_range in [(7,7), (8,9), (10,11), (12, 14), (15,18)]:
    eta_range_values = (histo_3d.GetXaxis().GetBinLowEdge(eta_range[0]), histo_3d.GetXaxis().GetBinUpEdge(eta_range[1]))
    # for pt_range in [(3,5), (6,10), (11,15), (16,20), (21,50)]:
    for pt_range in [(3,5), (6,7), (8,9), (10,11), (12,13), (14,15), (16,17), (18,19), (20,21), (22,50)]:
        pt_range_values = (histo_3d.GetYaxis().GetBinLowEdge(pt_range[0]), histo_3d.GetYaxis().GetBinUpEdge(pt_range[1]))
        print 'eta range: from eta {} (bin {}) to eta {} (bin {})'.format(eta_range_values[0], eta_range[0], eta_range_values[1], eta_range[1])
        print 'pt range: from pt {} [GeV] (bin {}) to pt {} [GeV] (bin {})'.format(pt_range_values[0], pt_range[0], pt_range_values[1], pt_range[1])
        hname = 'pt{}to{}_eta{}to{}'.format(pt_range_values[0], pt_range_values[1], eta_range_values[0], eta_range_values[1])
        respPlot = histo_3d.ProjectionZ(hname, eta_range[0], eta_range[1], pt_range[0], pt_range[1], '')
        respPlot.GetXaxis().SetRangeUser(0.7, 1.5)
        max_bin = respPlot.GetMaximumBin()
        max_value = respPlot.GetBinCenter(max_bin)
        rms_value = respPlot.GetRMS()
        respPlot.GetXaxis().SetRangeUser(0, 3)
        print '   max_value = {}, RMS = {}'.format(max_value, rms_value)
        quantile = array('d', [1])
        respPlot.GetQuantiles(1, quantile, array('d', [0.5]))

        k_l = 0.5
        k_r = 1.
        if pt_range_values[0] > 30 or eta_range[0] > 14:
            k_l = 1.
        #fitf = ROOT.TF1('myfunc', 'gaus')
        #fitf.SetParameter(0,0.93)
        draw([respPlot], labels=['PU0'], text=hname)

        result = respPlot.Fit('gaus','QERLS+', '', max_value-k_l*rms_value,  max_value+k_r*rms_value)
        result.Print()
        print '   mean = {}, sigma= {}'.format(result.GetParams()[1], result.GetParams()[2],)

        calib_reco_df= calib_reco_df.append({'samp_type': sample,
                                             'tp': tp_set,
                                             'eta_l': eta_range_values[0], 
                                             'eta_h': eta_range_values[1], 
                                             'pt_l': pt_range_values[0],
                                             'pt_h': pt_range_values[1],
                                             'peak': result.GetParams()[1],
                                             'avg': respPlot.GetMean(),
                                             'mdn': quantile[0]}, ignore_index=True)
        ROOT.gStyle.SetOptFit(11111)

eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 4.0 [GeV] (bin 3) to pt 10.0 [GeV] (bin 5)
   max_value = 0.885, RMS = 0.0543061688096
   mean = 0.896627667675, sigma= 0.0157968741773
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 10.0 [GeV] (bin 6) to pt 14.0 [GeV] (bin 7)
   max_value = 0.945, RMS = 0.0682880850795
   mean = 0.954614390379, sigma= 0.0314700517223
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 14.0 [GeV] (bin 8) to pt 18.0 [GeV] (bin 9)
   max_value = 0.915, RMS = 0.0582547836328
   mean = 0.927505250128, sigma= 0.0161300143943
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 18.0 [GeV] (bin 10) to pt 22.0 [GeV] (bin 11)
   max_value = 0.945, RMS = 0.0540486253496
   mean = 0.959404291602, sigma= 0.0166391048318
eta range: from eta 1.6 (bin 7) to eta 1.7 (bin 7)
pt range: from pt 22.0 [GeV] (bin 12) to pt 26.0 [GeV] (bin 13)
   max_value = 0.945, RMS = 0.055953618109
   mean = 0.95791

In [20]:
calib_reco_df[(calib_reco_df.samp_type == sample) & (calib_reco_df.tp == tp_set)]

samp_type         tp  eta_l  eta_h  pt_l   pt_h      peak       avg  \
150    photon  DEFMerged    1.6    1.7   4.0   10.0  0.896628  0.900405   
151    photon  DEFMerged    1.6    1.7  10.0   14.0  0.954614  0.934180   
152    photon  DEFMerged    1.6    1.7  14.0   18.0  0.927505  0.956507   
153    photon  DEFMerged    1.6    1.7  18.0   22.0  0.959404  0.961935   
154    photon  DEFMerged    1.6    1.7  22.0   26.0  0.957915  0.945423   
155    photon  DEFMerged    1.6    1.7  26.0   30.0  0.959201  0.956020   
156    photon  DEFMerged    1.6    1.7  30.0   34.0  0.942191  0.942541   
157    photon  DEFMerged    1.6    1.7  34.0   38.0  0.976623  0.965625   
158    photon  DEFMerged    1.6    1.7  38.0   42.0  0.972294  0.964138   
159    photon  DEFMerged    1.6    1.7  42.0  100.0  0.983894  0.958546   
160    photon  DEFMerged    1.7    1.9   4.0   10.0  0.933586  0.929423   
161    photon  DEFMerged    1.7    1.9  10.0   14.0  0.928864  0.938571   
162    photon  DEFMerged    1.7    1.9  14.0   18.0  0.959650  0.941640   
163    photon  DEFMerged    1.7    1.9  18.0   22.0  0.956283  0.939733   
164    photon  DEFMerged    1.7    1.9  22.0   26.0  0.956235  0.948699   
165    photon  DEFMerged    1.7    1.9  26.0   30.0  0.982847  0.952573   
166    photon  DEFMerged    1.7    1.9  30.0   34.0  0.959177  0.952615   
167    photon  DEFMerged    1.7    1.9  34.0   38.0  0.954185  0.947571   
168    photon  DEFMerged    1.7    1.9  38.0   42.0  0.972190  0.957941   
169    photon  DEFMerged    1.7    1.9  42.0  100.0  0.970978  0.948429   
170    photon  DEFMerged    1.9    2.1   4.0   10.0  0.928292  0.917842   
171    photon  DEFMerged    1.9    2.1  10.0   14.0  0.927368  0.924362   
172    photon  DEFMerged    1.9    2.1  14.0   18.0  0.956871  0.927821   
173    photon  DEFMerged    1.9    2.1  18.0   22.0  0.959714  0.946875   
174    photon  DEFMerged    1.9    2.1  22.0   26.0  0.959745  0.938130   
175    photon  DEFMerged    1.9    2.1  26.0   30.0  0.957938  0.940066   
176    photon  DEFMerged    1.9    2.1  30.0   34.0  0.957368  0.940537   
177    photon  DEFMerged    1.9    2.1  34.0   38.0  0.969502  0.942273   
178    photon  DEFMerged    1.9    2.1  38.0   42.0  0.962756  0.942310   
179    photon  DEFMerged    1.9    2.1  42.0  100.0  0.970986  0.950333   
180    photon  DEFMerged    2.1    2.4   4.0   10.0  0.925038  0.890702   
181    photon  DEFMerged    2.1    2.4  10.0   14.0  0.899548  0.913916   
182    photon  DEFMerged    2.1    2.4  14.0   18.0  0.925885  0.919565   
183    photon  DEFMerged    2.1    2.4  18.0   22.0  0.929056  0.933670   
184    photon  DEFMerged    2.1    2.4  22.0   26.0  0.958244  0.939328   
185    photon  DEFMerged    2.1    2.4  26.0   30.0  0.958226  0.939089   
186    photon  DEFMerged    2.1    2.4  30.0   34.0  0.955191  0.943585   
187    photon  DEFMerged    2.1    2.4  34.0   38.0  0.960994  0.939653   
188    photon  DEFMerged    2.1    2.4  38.0   42.0  0.954799  0.942789   
189    photon  DEFMerged    2.1    2.4  42.0  100.0  0.964653  0.945151   
190    photon  DEFMerged    2.4    2.8   4.0   10.0  0.881816  0.877562   
191    photon  DEFMerged    2.4    2.8  10.0   14.0  0.908943  0.899700   
192    photon  DEFMerged    2.4    2.8  14.0   18.0  0.917771  0.913761   
193    photon  DEFMerged    2.4    2.8  18.0   22.0  0.932537  0.924000   
194    photon  DEFMerged    2.4    2.8  22.0   26.0  0.933777  0.922282   
195    photon  DEFMerged    2.4    2.8  26.0   30.0  0.931201  0.928028   
196    photon  DEFMerged    2.4    2.8  30.0   34.0  0.932739  0.935000   
197    photon  DEFMerged    2.4    2.8  34.0   38.0  0.946771  0.935280   
198    photon  DEFMerged    2.4    2.8  38.0   42.0  0.951102  0.934518   
199    photon  DEFMerged    2.4    2.8  42.0  100.0  0.962037  0.941980   

          mdn  
150  0.898333  
151  0.943235  
152  0.951250  
153  0.962000  
154  0.948158  
155  0.958750  
156  0.946500  
157  0.971053  
158  0.969474  
159  0.970662  
16

## Compare calibration results

In [24]:
eta_bin_l = 1.9
eta_bin_h = 2.1

sample = 'photon'
tp_set = 'DEF'

graphs = []
labels = []

calib_reco_df['pt'] = calib_reco_df.pt_l+(calib_reco_df.pt_h - calib_reco_df.pt_l)/2.

calib_reco_df_sel = calib_reco_df[(calib_reco_df.samp_type == sample) & (calib_reco_df.tp == tp_set) & (calib_reco_df.eta_l == eta_bin_l) & (calib_reco_df.eta_h == eta_bin_h)]
# print calib_reco_df_sel

ph_DEF_peak = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.peak.values)
ph_DEF_peak.SetMarkerStyle(7)
ph_DEF_peak.SetMarkerColor(1)

# graphs.append(g1)
# labels.append('peak')

ph_DEF_avg = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.avg.values)
ph_DEF_avg.SetMarkerStyle(7)
ph_DEF_avg.SetMarkerColor(2)

# graphs.append(g2)
# labels.append('avg')

ph_DEF_mdn = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.mdn.values)
ph_DEF_mdn.SetMarkerStyle(7)
ph_DEF_mdn.SetMarkerColor(3)

# graphs.append(g3)
# labels.append('mdn')

tp_set = 'DEFMerged'

calib_reco_df['pt'] = calib_reco_df.pt_l+(calib_reco_df.pt_h - calib_reco_df.pt_l)/2.

calib_reco_df_sel = calib_reco_df[(calib_reco_df.samp_type == sample) & (calib_reco_df.tp == tp_set) & (calib_reco_df.eta_l == eta_bin_l) & (calib_reco_df.eta_h == eta_bin_h)]
# print calib_reco_df_sel

ph_Merged_peak = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.peak.values)
ph_Merged_peak.SetMarkerStyle(7)
ph_Merged_peak.SetMarkerColor(4)

# graphs.append(g1)
# labels.append('peak')

ph_Merged_avg = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.avg.values)
ph_Merged_avg.SetMarkerStyle(7)
ph_Merged_avg.SetMarkerColor(5)

# graphs.append(g2)
# labels.append('avg')

ph_Merged_mdn = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.mdn.values)
ph_Merged_mdn.SetMarkerStyle(7)
ph_Merged_mdn.SetMarkerColor(6)

# print calib_reco_df_sel.pt.values
# print calib_reco_df_sel.peak.values
# print calib_reco_df_sel.avg.values
# print calib_reco_df_sel.mdn.values

# draw(graphs, labels=labels, text='{}, {}'.format(sample, tp_set), min_y=0., max_y=1.1)
# g2.Draw("same,P")
# g3.Draw("same,P")





In [25]:
eta_bin_l = 1.9
eta_bin_h = 2.1

sample = 'ele'
tp_set = 'DEF'

graphs = []
labels = []

calib_reco_df['pt'] = calib_reco_df.pt_l+(calib_reco_df.pt_h - calib_reco_df.pt_l)/2.

calib_reco_df_sel = calib_reco_df[(calib_reco_df.samp_type == sample) & (calib_reco_df.tp == tp_set) & (calib_reco_df.eta_l == eta_bin_l) & (calib_reco_df.eta_h == eta_bin_h)]
# print calib_reco_df_sel

ele_DEF_peak = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.peak.values)
ele_DEF_peak.SetMarkerStyle(7)
ele_DEF_peak.SetMarkerColor(1)

ele_DEF_avg = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.avg.values)
ele_DEF_avg.SetMarkerStyle(7)
ele_DEF_avg.SetMarkerColor(2)

ele_DEF_mdn = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.mdn.values)
ele_DEF_mdn.SetMarkerStyle(7)
ele_DEF_mdn.SetMarkerColor(3)


tp_set = 'DEFMerged'

graphs = []
labels = []

calib_reco_df['pt'] = calib_reco_df.pt_l+(calib_reco_df.pt_h - calib_reco_df.pt_l)/2.

calib_reco_df_sel = calib_reco_df[(calib_reco_df.samp_type == sample) & (calib_reco_df.tp == tp_set) & (calib_reco_df.eta_l == eta_bin_l) & (calib_reco_df.eta_h == eta_bin_h)]
# print calib_reco_df_sel

ele_Merged_peak = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.peak.values)
ele_Merged_peak.SetMarkerStyle(7)
ele_Merged_peak.SetMarkerColor(1)

ele_Merged_avg = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.avg.values)
ele_Merged_avg.SetMarkerStyle(7)
ele_Merged_avg.SetMarkerColor(2)

ele_Merged_mdn = ROOT.TGraph(len(calib_reco_df_sel.pt.values), calib_reco_df_sel.pt.values, calib_reco_df_sel.mdn.values)
ele_Merged_mdn.SetMarkerStyle(7)
ele_Merged_mdn.SetMarkerColor(3)


# print calib_reco_df_sel.pt.values
# print calib_reco_df_sel.peak.values
# print calib_reco_df_sel.avg.values
# print calib_reco_df_sel.mdn.values




In [44]:
def draw(histograms,
         labels,
         options='',
         norm=False,
         logy=False,
         min_y=None,
         max_y=None,
         text=None,
         y_axis_label=None,
         x_axis_label=None,
         v_lines=None,
         h_lines=None,
         do_stats=False,
         do_profile=False,
         do_ratio=False):
    global colors
    global stuff
    global p_idx


    # 0 - determine kind and # of histos
    n_histos = len(histograms)
    if n_histos == 0:
        print '[draw]**ERROR: empy histo list'
        return

    histo_class = histograms[0].ClassName()

    # 1 - check argument consisntency
    if 'TH2' not in histo_class and do_profile:
        print '[draw]**ERROR: do_profile set for histo of class: {}'.format(histo_class)
        return

    # TH1 histograms are overlayed
    # TH2 histograms are drawn side by side in the same canvas
    overlay = True
    if n_histos > 1:
        if 'TH2' in histo_class or 'TH3' in histo_class:
            overlay = False

    # 2 - determine canvas properties
    xdiv = 0
    ydiv = 0
    c_width = 800
    c_height = 600
    # do_ratio = False

    if do_ratio:
        c_height = 800

    if not overlay:
        xdiv = 2
        c_width = 1000.
        ydiv = math.ceil(float(n_histos)/2)
        c_height = 500*ydiv
    canvas = newCanvas(name=None,
                       title=None,
                       height=int(c_height),
                       width=int(c_width),
                       xdiv=int(xdiv),
                       ydiv=int(ydiv))
    if overlay:
        canvas.SetRightMargin(0.30)

    canvas.cd()
    leg = getLegend()

    drawn_histos = []
    # drawn_histos = histograms
    for hidx, hist in enumerate(histograms):
        opt = options
        if 'TGraph' not in histo_class:
            hist.SetStats(do_stats)
        else:
            opt = 'P'+options
        if overlay:
            hist.SetLineColor(colors[hidx])
            if 'TGraph' in histo_class:
                hist.SetMarkerColor(colors[hidx])
            if hidx:
                opt = 'same,'+opt
            else:
                if 'TGraph' in histo_class:
                    opt = opt+'A'
        else:
            canvas.cd(hidx+1)
        print hidx, opt
        d_hist = hist
        if norm:
            d_hist = hist.DrawNormalized(opt, 1.)
        else:
            hist.Draw(opt)

        if do_profile:
            profname = d_hist.GetName()+'_prof_'+str(p_idx)
            p_idx += 1
            firstbin = 1
            lastbin = -1
            prof = d_hist.ProfileX(profname, firstbin, lastbin, 's')
            prof.SetMarkerColor(2)
            prof.SetLineColor(2)
            prof.Draw('same')

        if overlay:
            if 'TGraph' not in histo_class:
                leg.AddEntry(hist, labels[hidx], 'l')
            else:
                leg.AddEntry(hist, labels[hidx], 'P')
        else:
            if text:
                newtext = '{}: {}'.format(labels[hidx], text)
                rtext = getText(newtext, 0.15, 0.85)
                rtext.Draw('same')
        drawn_histos.append(d_hist)

    if do_ratio:
        h_ratio = ROOT.TRatioPlot(drawn_histos[0], drawn_histos[1])
        stuff.append(h_ratio)
        h_ratio.Draw()

        pad = canvas.cd(1)
        h_ratio.GetUpperPad().SetBottomMargin(0)
        h_ratio.GetUpperPad().SetRightMargin(0.3)
        if logy:
            h_ratio.GetUpperPad().SetLogy()
        pad.Update()
        pad = canvas.cd(2)
        h_ratio.GetLowerPad().SetTopMargin(0)
        h_ratio.GetLowerPad().SetRightMargin(0.3)
        pad.Update()
        # hratio.GetLowerRefGraph().GetYaxis().SetRangeUser(-6, 6)

    canvas.Update()

    # we now set the axis properties
    max_value = max_y
    min_value = min_y

    if min_y is None:
        min_value = min([hist.GetBinContent(hist.GetMinimumBin()) for hist in drawn_histos])
    if max_y is None:
        max_value = max([hist.GetBinContent(hist.GetMaximumBin()) for hist in drawn_histos])*1.2
    # print min_value, max_value

    for hist in drawn_histos:
        hist.GetYaxis().SetRangeUser(min_value, max_value)
        if y_axis_label:
            hist.GetYaxis().SetTitle(y_axis_label)
        if x_axis_label:
            hist.GetXaxis().SetTitle(x_axis_label)

    canvas.Draw()

    # we draw additional stuff if needed
    if overlay:
        canvas.cd()
        leg.Draw()
        if text:
            rtext = getText(text, 0.15, 0.85)
            rtext.Draw("same")

    pad_range = range(0, 1)
    if not overlay:
        pad_range = range(1, len(histograms)+1)

    for pad_id in pad_range:
        canvas.cd(pad_id)
        if v_lines:
            for v_line_x in v_lines:
                aline = ROOT.TLine(v_line_x, ROOT.gPad.GetUymin(), v_line_x,  ROOT.gPad.GetUymax())
                aline.SetLineStyle(2)
                aline.Draw("same")
                stuff.append(aline)
        if h_lines:
            for h_line_y in h_lines:
                aline = ROOT.TLine(ROOT.gPad.GetUxmin(), h_line_y, ROOT.gPad.GetUxmax(),  h_line_y)
                aline.SetLineStyle(2)
                aline.Draw("same")
                stuff.append(aline)
        if logy:
            if not do_ratio:
                ROOT.gPad.SetLogy()

        ROOT.gPad.Update()
    canvas.Update()
    canvas.Draw()

    return canvas


In [37]:
draw([ph_Merged_peak, ph_Merged_avg, ph_Merged_mdn], labels=['peak', 'avg', 'mdn'], text='photons, Merged', min_y=0., max_y=1.1)



0 PA
1 same,P
2 same,P


<ROOT.TCanvas object ("c_d7b1dc") at 0x7fef7aacd950>

In [38]:
draw([ph_DEF_peak, ph_DEF_avg, ph_DEF_mdn], labels=['peak', 'avg', 'mdn'], text='photons, DEF', min_y=0., max_y=1.1)


0 PA
1 same,P
2 same,P


<ROOT.TCanvas object ("c_96f185") at 0x7fef7a986ee0>

In [39]:
draw([ph_DEF_peak, ph_Merged_peak], labels=['DEF', 'Merged'], text='photons, peak', min_y=0., max_y=1.1)


0 PA
1 same,P


<ROOT.TCanvas object ("c_b355aa") at 0x7fef7abb7300>

In [40]:
draw([ele_Merged_peak, ele_Merged_avg, ele_Merged_mdn], labels=['peak', 'avg', 'mdn'], text='ele, Merged', min_y=0., max_y=1.1)


0 PA
1 same,P
2 same,P


<ROOT.TCanvas object ("c_234c61") at 0x7fef7abb2930>

In [41]:
draw([ele_DEF_peak, ele_DEF_avg, ele_DEF_mdn], labels=['peak', 'avg', 'mdn'], text='ele, DEF', min_y=0., max_y=1.1)


0 PA
1 same,P
2 same,P


<ROOT.TCanvas object ("c_65510f") at 0x7fef7ac7e0a0>

In [48]:
draw([ph_DEF_peak, ph_DEF_avg, ph_DEF_mdn, ph_Merged_peak, ph_Merged_avg, ph_Merged_mdn], 
     labels=['peak DEF', 'avg DEF', 'mdn DEF', 'peak Merged', 'avg Merged', 'mdn Merged'], text='photons', min_y=0., max_y=1.1)


0 PA
1 same,P
2 same,P
3 same,P
4 same,P
5 same,P


<ROOT.TCanvas object ("c_0fc6b5") at 0x7fef7abb7da0>

In [49]:
draw([ele_DEF_peak, ele_DEF_mdn, ele_Merged_peak, ele_Merged_mdn], 
     labels=['peak DEF', 'mdn DEF', 'peak Merged', 'mdn Merged'], text='ele', min_y=0., max_y=1.1)


0 PA
1 same,P
2 same,P
3 same,P


<ROOT.TCanvas object ("c_48a9a5") at 0x7fef7aacd350>

In [50]:
draw([ele_DEF_peak, ele_DEF_mdn, ph_DEF_peak, ph_DEF_mdn], 
     labels=['peak ele', 'mdn ele', 'peak ph', 'mdn ph'], text='DEF', min_y=0., max_y=1.1)


0 PA
1 same,P
2 same,P
3 same,P


<ROOT.TCanvas object ("c_f2bb53") at 0x7fef7ad21f10>

In [51]:
draw([ele_Merged_peak, ele_Merged_mdn, ph_Merged_peak, ph_Merged_mdn], 
     labels=['peak ele', 'mdn ele', 'peak ph', 'mdn ph'], text='Merged', min_y=0., max_y=1.1)


0 PA
1 same,P
2 same,P
3 same,P


<ROOT.TCanvas object ("c_d0b8b2") at 0x7fef7a9808d0>

In [12]:
class HistoTemplate(object):
    def __init__(self, histo):
        self._histo = histo
        
    def __call__(self, x, par):
        xx = par[1] * (x[0] - par[2])
        xMin = self._histo.GetBinCenter(1)
        xMax = self._histo.GetBinCenter(self._histo.GetNbinsX())
    
        if xx < xMin or xx >= xMax:
            return 1.e-10
        else:
            bin = self._histo.FindBin(xx)
            bin1 = 0
            bin1 = 0
            
            if xx >= self._histo.GetBinCenter(bin):
                bin1 = bin
                bin2 = bin+1
            else:
                bin1 = bin-1
                bin2 = bin
            
            x1 = self._histo.GetBinCenter(bin1)
            y1 = self._histo.GetBinContent(bin1)
            x2 = self._histo.GetBinCenter(bin2)
            y2 = self._histo.GetBinContent(bin2)
            
            m = 1. * (y2 - y1) / (x2 - x1)
            
            if (y1 + m * (xx - x1)) < 1.e-10:
                return 1.e-10
            
            return par[0] * par[1] * (y1 + m * (xx - x1))
        return 1.e-10
            
        

In [13]:
def double_goussian(x, params):
    if x[0]>= params[0]:
        return params[1]*ROOT.TMath.Gaus(x[0], params[0], params[2])
    else:
        return (params[1])*(ROOT.TMath.Gaus(x[0], params[0], params[3])+(params[4]+x[0]*params[5]+params[6]*x[0]*x[0]))
fitf = ROOT.TF1('myfunc', double_goussian, 0, 3, 7)
# fitf.SetParNames('mean', "norm", 'sigma_p', 'sigma_m', 'norm_l')
fitf.SetParameters(1,1,0.1,0.2, 1, 3, 4)
c = newCanvas()
fitf.Draw()
c.Draw()

In [14]:
particle = 'eleC'
tp_set = 'DEF_em'

# pt_bins = [(1, 4), (5, 9), (10, 14), (15, 19), (20, 50)]
pt_bins = [(1, 4), (5, 9), (10, 14), (15, 19), (20, 50)]

hsets, labels, text = hplot.get_histo(histos.HistoSetReso, 'ele', ['PU0', 'PU200'], 'DEF', 'Em', 'GENEtaC') 
hByTPset = [his.hreso.h_ptRespVpt for his in hsets]
histogram = hByTPset[0]



In [15]:
template = HistoTemplate(histogram.ProjectionY(uuid.uuid4().hex[:6], 20, 50))
fitf = ROOT.TF1('myfunc', template, 0, 3, 3)
fitf.SetParNames('norm', 'scale', 'shift')
c = newCanvas()
# fitf.SetParameters(1.,1.,0.)
# fitf.Draw()
fitf.SetParameters(10.,3.,1.5)
fitf.Draw()
c.Draw()    


In [16]:
for pt_bin in pt_bins:
#     project_hist
    project_hist = histogram.ProjectionY(uuid.uuid4().hex[:6], pt_bin[0], pt_bin[1])
    fitf.SetParameters(1.,1.,0.)
#     fitf.FixParameter(2, 0)
    project_hist.Fit('gaus','SE', '',0.9,1.)
    draw(project_hist, options='hist')

 FCN=1.42716e-07 FROM MINOS     STATUS=FAILURE       117 CALLS        1221 TOTAL
                     EDM=3.72522e-07    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant     3.78042e+02   1.95170e+03   1.53085e+03   0.00000e+00
   2  Mean         7.75373e-01   5.83170e-01  -7.24279e+00   0.00000e+00
   3  Sigma        9.62504e-02   1.61127e-01   1.61127e-01  -1.72236e+02
 FCN=5.25198e-09 FROM MINOS     STATUS=SUCCESSFUL    167 CALLS         711 TOTAL
                     EDM=1.05009e-08    STRATEGY= 1      ERROR MATRIX ACCURATE 
  EXT PARAMETER                                   STEP         FIRST   
  NO.   NAME      VALUE            ERROR          SIZE      DERIVATIVE 
   1  Constant     1.15273e+03   1.45902e+02   1.79522e-01   6.37958e-06
   2  Mean         8.88382e-01   2.68253e-02  -2.28828e-05   8.76444e-02
   3  Sigma        7.0765

In [17]:
from array import array
calibFactors_hist = ROOT.TH2F('calibFactors_hist', 'calib factor', 5, array('d',[0., 10., 20., 30., 40., 100.]), 3, array('d',[1.52, 1.7, 2.4, 2.8]))


In [18]:
#draw(calibFactors_hist)

In [19]:
calibFactors_df = pd.DataFrame(columns=['eta_l', 'eta_h', 'pt_l', 'pt_h', 'calib'])

In [59]:
def gaussfit(project_hist):
    max_bin = project_hist.GetMaximumBin()
    max_value = project_hist.GetBinCenter(max_bin)
    rms_value = project_hist.GetRMS()
    
    k_l = 0.5
    k_r = 1.
#         if(gen_sel) == 'eleD':
#             k_l = 1.5
#             k_r = 2.
    print '   max_value = {}, RMS = {}'.format(max_value, rms_value)
    result = project_hist.Fit('gaus','QERLS+', '', max_value-k_l*rms_value,  max_value+k_r*rms_value)
    # result.Print()
    print '   mean = {}, sigma = {}'.format(result.GetParams()[1], result.GetParams()[2])
    func = project_hist.GetFunction("gaus")
    print '   NDF = {}, chi2 = {}, prob = {}'.format(func.GetNDF(), func.GetChisquare(), func.GetProb())
    return result 


def gausstailfit(project_hist):
    max_bin = project_hist.GetMaximumBin()
    max_value = project_hist.GetBinCenter(max_bin)
    rms_value = project_hist.GetRMS()

    def gausstail(x, p):
#         // [Constant] * ROOT::Math::crystalball_function(x, [Alpha], [N], [Sigma], [Mean])
        return p[0] * ROOT.Math.crystalball_function(x[0], p[3], p[4], p[2], p[1])
    
    fitf = ROOT.TF1('gausstail', gausstail, 0, 3, 5)
    fitf.SetParNames('norm', 'mean', 'sigma', 'alpha', 'n')
#     fitf.FixParameter(0, 1.)
    fitf.SetParLimits(1, 0.8, 1.)

    fitf.SetParameters(project_hist.Integral(),max_value,rms_value, 1, 1)
#     c = newCanvas()
#     fitf.Draw()
#     c.Draw()
    print '   max_value = {}, RMS = {}'.format(max_value, rms_value)
    result = project_hist.Fit('gausstail','QERLS+')
    result.Print()
    print '   mean = {}, sigma = {}'.format(result.GetParams()[1], result.GetParams()[2])
#     func = project_hist.GetFunction("gaus")
    print '   NDF = {}, chi2 = {}, prob = {}'.format(fitf.GetNDF(), fitf.GetChisquare(), fitf.GetProb())
    return result 


In [60]:
def gausstail(x, p):
#         // [Constant] * ROOT::Math::crystalball_function(x, [Alpha], [N], [Sigma], [Mean])
    return p[0] * ROOT.Math.crystalball_function(x[0], p[3], p[4], p[2], p[1])

fitf = ROOT.TF1('gausstail', gausstail, 0, 3, 5)
fitf.SetParNames('norm', 'mean', 'sigma', 'alpha', 'n')
fitf.SetParameters(1,0.85,0.1, 1, 1)
c = newCanvas()
fitf.Draw()
c.Draw()

In [61]:
eta_ranges = {'GENEtaB': (1.52, 1.7),
              'GENEtaC': (1.7, 2.4),
              'GENEtaD': (2.4, 2.8)}

tp_set = 'DEF'
# pt_bins = [(1, 4), (5, 9), (10, 14), (15, 19), (20, 50)]
pt_bins = [(1, 5), (6, 10), (11, 15), (16, 20), (21, 50)]

for id_p,gen_sel in enumerate(['GENEtaB', 'GENEtaC','GENEtaD']):

    hsets, labels, text = hplot.get_histo(histos.HistoSetReso, 'ele', ['PU0', 'PU200'], 'DEF', 'Em', gen_sel) 
    hByTPset = [his.hreso.h_ptRespVpt for his in hsets]
    histogram = hByTPset[0]
    draw(histogram, options='COLZ', text=text)
    for id_pt,pt_bin in enumerate(pt_bins):
        pt_bin_low = histogram.GetXaxis().GetBinLowEdge(pt_bin[0])
        pt_bin_up = histogram.GetXaxis().GetBinUpEdge(pt_bin[1])
        print '==== ETA region: {}, {} < pT < {}'.format(text, pt_bin_low, pt_bin_up)

        project_hist = histogram.ProjectionY(uuid.uuid4().hex[:6], pt_bin[0], pt_bin[1])
        project_hist.GetXaxis().SetRangeUser(0.53, 1.5)
#         max_bin = project_hist.GetMaximumBin()
#         max_value = project_hist.GetBinCenter(max_bin)
#         rms_value = project_hist.GetRMS()
#         project_hist.GetXaxis().SetRangeUser(0, 3)
#         print '   max_value = {}, RMS = {}'.format(max_value, rms_value)
    
#         k_l = 0.5
#         k_r = 1.
#         if(gen_sel) == 'eleD':
#             k_l = 1.5
#             k_r = 2.
#         #fitf = ROOT.TF1('myfunc', 'gaus')
#         #fitf.SetParameter(0,0.93)
#         result = project_hist.Fit('gaus','QERLS+', '', max_value-k_l*rms_value,  max_value+k_r*rms_value)
#         result.Print()
#         print '   mean = {}, sigma = {}'.format(result.GetParams()[1], result.GetParams()[2])
        result = gausstailfit(project_hist)
        draw(project_hist, options='hist', text=text)
        calibFactors_hist.SetBinContent(id_pt+1, id_p+1, result.GetParams()[1])
        calibFactors_df= calibFactors_df.append({'eta_l': eta_ranges[gen_sel][0], 
                                                 'eta_h': eta_ranges[gen_sel][1], 
                                                 'pt_l': pt_bin_low, 
                                                 'pt_h': pt_bin_up, 
                                                 'calib': result.GetParams()[1]}, ignore_index=True)
#     bin_min = histogram.GetBinWithContent(pt_bin[0])
#     bin_max = histogram.GetBinWithContent(pt_bin[1])-1
#     print 'pt_bins: {} bin # ({}, {})'.format(pt_bin, bin_min, bin_max)



# #drawGaussFit(hByTPset[0], 3, 0, 3)
# draw(hByTPset[0])
# fitf = ROOT.TF1('myfunc', 'crystalball')
# fitf.SetParameter(1,0.93)
# #fitf.SetParameter('Constant', hByTPset[0].Integral())

# # fitf.SetParameter('Mean', 0.93)
# # fitf.SetParameter('Sigma', hByTPset[0].GetRMS())

# #fitf.SetParameter(2, 5)

# hByTPset[0].Fit('myfunc','VLE', '', 0, 0.94 )
# print hByTPset[0].GetName()
# print hByTPset[0].GetEntries()

==== ETA region: NNDR, EGId, 1.52 < |#eta^{GEN}| <= 1.7, 0.0 < pT < 10.0
   max_value = 0.885, RMS = 0.139516473545
   mean = 0.874038887949, sigma = 0.0855287266943
   NDF = 28, chi2 = 19.4004069562, prob = 0.885327538384
==== ETA region: NNDR, EGId, 1.52 < |#eta^{GEN}| <= 1.7, 10.0 < pT < 20.0
   max_value = 0.885, RMS = 0.147195689314
   mean = 0.981688177302, sigma = 0.0351567808895
   NDF = 28, chi2 = 175.22463896, prob = 3.0080985985e-23
==== ETA region: NNDR, EGId, 1.52 < |#eta^{GEN}| <= 1.7, 20.0 < pT < 30.0
   max_value = 0.975, RMS = 0.146290475022
   mean = 0.943059250435, sigma = 0.0592136625864
   NDF = 28, chi2 = 151.495666226, prob = 6.62305215842e-19
==== ETA region: NNDR, EGId, 1.52 < |#eta^{GEN}| <= 1.7, 30.0 < pT < 40.0
   max_value = 0.945, RMS = 0.136410496009
   mean = 0.960601923389, sigma = 0.0487202155224
   NDF = 28, chi2 = 30.8909401375, prob = 0.321944617947
==== ETA region: NNDR, EGId, 1.52 < |#eta^{GEN}| <= 1.7, 40.0 < pT < 100.0
   max_value = 0.975, RMS 

In [62]:

draw(calibFactors_hist, options='COLZ')


In [ ]:
calibFactors_df

In [ ]:
with open('calib_v53_v0.json', 'w') as f:
    f.write(calibFactors_df.to_json(orient='split'))

In [ ]:
calibFactors_reco_df = pd.DataFrame(columns=['eta_l', 'eta_h', 'pt_l', 'pt_h', 'calib'])


hsets, labels, text = hplot.get_histo(histos.HistoSetReso, 'ele', ['PU0', 'PU200'], 'DEF', 'Em', 'GEN') 
hByTPset = [his.hreso.h_ptRespVetaVptL1 for his in hsets]
drawSeveral(hByTPset, labels=labels)
histo_3d = hByTPset[0]
#         for eta_range in [(7,7), (8,11), (12, 14)]:
for eta_range in [(7,7), (8,9), (10,11), (12, 14), (15,18)]:
    eta_range_values = (histo_3d.GetXaxis().GetBinLowEdge(eta_range[0]), histo_3d.GetXaxis().GetBinUpEdge(eta_range[1]))
    # for pt_range in [(3,5), (6,10), (11,15), (16,20), (21,50)]:
    for pt_range in [(3,5), (6,7), (8,9), (10,11), (12,13), (14,15), (16,17), (18,19), (20,21), (22,50)]:
        pt_range_values = (histo_3d.GetYaxis().GetBinLowEdge(pt_range[0]), histo_3d.GetYaxis().GetBinUpEdge(pt_range[1]))
        print 'eta range: from eta {} (bin {}) to eta {} (bin {})'.format(eta_range_values[0], eta_range[0], eta_range_values[1], eta_range[1])
        print 'pt range: from pt {} [GeV] (bin {}) to pt {} [GeV] (bin {})'.format(pt_range_values[0], pt_range[0], pt_range_values[1], pt_range[1])
        hname = 'pt{}to{}_eta{}to{}'.format(pt_range_values[0], pt_range_values[1], eta_range_values[0], eta_range_values[1])
        respPlot = histo_3d.ProjectionZ(hname, eta_range[0], eta_range[1], pt_range[0], pt_range[1], '')

        respPlot.GetXaxis().SetRangeUser(0.7, 1.5)
        max_bin = respPlot.GetMaximumBin()
        max_value = respPlot.GetBinCenter(max_bin)
        rms_value = respPlot.GetRMS()
        respPlot.GetXaxis().SetRangeUser(0, 3)
        print '   max_value = {}, RMS = {}'.format(max_value, rms_value)

        k_l = 0.5
        k_r = 1.
        if pt_range_values[0] > 30 or eta_range[0] > 14:
            k_l = 1.
        #fitf = ROOT.TF1('myfunc', 'gaus')
        #fitf.SetParameter(0,0.93)
        result = respPlot.Fit('gaus','QERLS+', '', max_value-k_l*rms_value,  max_value+k_r*rms_value)
        result.Print()
        print '   mean = {}, sigma= {}'.format(result.GetParams()[1], result.GetParams()[2],)

        calibFactors_reco_df= calibFactors_reco_df.append({'eta_l': eta_range_values[0], 
                                                           'eta_h': eta_range_values[1], 
                                                           'pt_l': pt_range_values[0],
                                                           'pt_h': pt_range_values[1],
                                                           'calib': result.GetParams()[1]}, ignore_index=True)
        drawSame([respPlot], labels=['PU0'], text=hname)
        ROOT.gStyle.SetOptFit(11111)


In [33]:
calibFactors_reco_df

eta_l  eta_h  pt_l   pt_h     calib
0     1.6    1.7   4.0   10.0  0.778916
1     1.6    1.7  10.0   14.0  0.820097
2     1.6    1.7  14.0   18.0  0.895718
3     1.6    1.7  18.0   22.0  0.938889
4     1.6    1.7  22.0   26.0  0.931578
5     1.6    1.7  26.0   30.0  0.971356
6     1.6    1.7  30.0   34.0  0.939163
7     1.6    1.7  34.0   38.0  0.957731
8     1.6    1.7  38.0   42.0  0.942559
9     1.6    1.7  42.0  100.0  0.967016
10    1.7    1.9   4.0   10.0  0.846952
11    1.7    1.9  10.0   14.0  0.887712
12    1.7    1.9  14.0   18.0  0.906317
13    1.7    1.9  18.0   22.0  0.943263
14    1.7    1.9  22.0   26.0  0.939927
15    1.7    1.9  26.0   30.0  0.942948
16    1.7    1.9  30.0   34.0  0.949723
17    1.7    1.9  34.0   38.0  0.944230
18    1.7    1.9  38.0   42.0  0.942230
19    1.7    1.9  42.0  100.0  0.960713
20    1.9    2.1   4.0   10.0  0.865722
21    1.9    2.1  10.0   14.0  0.904167
22    1.9    2.1  14.0   18.0  0.919248
23    1.9    2.1  18.0   22.0  0.933113
24    1.9    2.1  22.0   26.0  0.938491
25    1.9    2.1  26.0   30.0  0.942763
26    1.9    2.1  30.0   34.0  0.941647
27    1.9    2.1  34.0   38.0  0.938493
28    1.9    2.1  38.0   42.0  0.940588
29    1.9    2.1  42.0  100.0  0.957647
30    2.1    2.4   4.0   10.0  0.876237
31    2.1    2.4  10.0   14.0  0.906254
32    2.1    2.4  14.0   18.0  0.913375
33    2.1    2.4  18.0   22.0  0.918462
34    2.1    2.4  22.0   26.0  0.924029
35    2.1    2.4  26.0   30.0  0.933929
36    2.1    2.4  30.0   34.0  0.940036
37    2.1    2.4  34.0   38.0  0.935934
38    2.1    2.4  38.0   42.0  0.939956
39    2.1    2.4  42.0  100.0  0.960463
40    2.4    2.8   4.0   10.0  0.858574
41    2.4    2.8  10.0   14.0  0.887637
42    2.4    2.8  14.0   18.0  0.907584
43    2.4    2.8  18.0   22.0  0.917303
44    2.4    2.8  22.0   26.0  0.928498
45    2.4    2.8  26.0   30.0  0.928893
46    2.4    2.8  30.0   34.0  0.935166
47    2.4    2.8  34.0   38.0  0.940684
48    2.4    2.8  38.0   42.0  0.942683
49    2.4    2.8  42.0  100.0  0.958354

In [34]:
with open('calib__v53_v2.json', 'w') as f:
    f.write(calibFactors_reco_df.to_json())

## read and plot the calibration factors

In [35]:
import pandas as pd
calibFactors_reco_df = pd.read_json('calib__v53_v2.json')

In [36]:
calibFactors_reco_df


calib  eta_h  eta_l  pt_h  pt_l
0   0.778916    1.7    1.6    10     4
1   0.820097    1.7    1.6    14    10
10  0.846952    1.9    1.7    10     4
11  0.887712    1.9    1.7    14    10
12  0.906317    1.9    1.7    18    14
13  0.943263    1.9    1.7    22    18
14  0.939927    1.9    1.7    26    22
15  0.942948    1.9    1.7    30    26
16  0.949723    1.9    1.7    34    30
17  0.944230    1.9    1.7    38    34
18  0.942230    1.9    1.7    42    38
19  0.960713    1.9    1.7   100    42
2   0.895718    1.7    1.6    18    14
20  0.865722    2.1    1.9    10     4
21  0.904167    2.1    1.9    14    10
22  0.919248    2.1    1.9    18    14
23  0.933113    2.1    1.9    22    18
24  0.938491    2.1    1.9    26    22
25  0.942763    2.1    1.9    30    26
26  0.941647    2.1    1.9    34    30
27  0.938493    2.1    1.9    38    34
28  0.940588    2.1    1.9    42    38
29  0.957647    2.1    1.9   100    42
3   0.938889    1.7    1.6    22    18
30  0.876237    2.4    2.1    10     4
31  0.906254    2.4    2.1    14    10
32  0.913375    2.4    2.1    18    14
33  0.918462    2.4    2.1    22    18
34  0.924029    2.4    2.1    26    22
35  0.933929    2.4    2.1    30    26
36  0.940036    2.4    2.1    34    30
37  0.935934    2.4    2.1    38    34
38  0.939956    2.4    2.1    42    38
39  0.960463    2.4    2.1   100    42
4   0.931578    1.7    1.6    26    22
40  0.858574    2.8    2.4    10     4
41  0.887637    2.8    2.4    14    10
42  0.907584    2.8    2.4    18    14
43  0.917303    2.8    2.4    22    18
44  0.928498    2.8    2.4    26    22
45  0.928893    2.8    2.4    30    26
46  0.935166    2.8    2.4    34    30
47  0.940684    2.8    2.4    38    34
48  0.942683    2.8    2.4    42    38
49  0.958354    2.8    2.4   100    42
5   0.971356    1.7    1.6    30    26
6   0.939163    1.7    1.6    34    30
7   0.957731    1.7    1.6    38    34
8   0.942559    1.7    1.6    42    38
9   0.967016    1.7    1.6   100    42

In [37]:
import numpy as np

bins_eta = np.sort(calibFactors_reco_df['eta_l'].unique())
bins_eta = np.append(bins_eta, np.sort(calibFactors_reco_df['eta_h'].unique())[-1])
bins_eta

array([ 1.6,  1.7,  1.9,  2.1,  2.4,  2.8])

In [38]:
bins_pt = np.sort(calibFactors_reco_df['pt_l'].unique())
bins_pt = np.append(bins_pt, np.sort(calibFactors_reco_df['pt_h'].unique())[-1])
bins_pt

array([  4,  10,  14,  18,  22,  26,  30,  34,  38,  42, 100])

In [46]:

print len(bins_eta)-1
print len(bins_pt)-1
from array import array
calibFactors_hist = ROOT.TH2F('calibFactors_hist', 
                              'calib factor (E_{L1}/E_{GEN}); #eta^{L1}; p_{T}^{L1} [GeV];', 
                              len(bins_eta)-1, array('d',bins_eta), 
                              len(bins_pt)-1,array('d', bins_pt))


calibFactors_hist

5
10


<ROOT.TH2F object ("calibFactors_hist") at 0x7fc5a0949400>

Warning in <TFile::Append>: Replacing existing TH1: calibFactors_hist (Potential memory leak).


In [47]:

for bin_eta_id,eta_bin in enumerate(bins_eta[:-1]):
    for bin_pt_id,pt_bin in enumerate(bins_pt[:-1]):
        corr = calibFactors_reco_df[(calibFactors_reco_df.eta_l <= eta_bin) & (calibFactors_reco_df.eta_h > eta_bin) & (calibFactors_reco_df.pt_l <= pt_bin) & (calibFactors_reco_df.pt_h > pt_bin)]
        #print corr
        print 'ix: {}, x: {}, iy: {}, y: {}, value: {}'.format(bin_eta_id,eta_bin, bin_pt_id, pt_bin, corr['calib'].iloc[0])
        calibFactors_hist.SetBinContent(bin_eta_id+1, bin_pt_id+1, corr['calib'].iloc[0])

ix: 0, x: 1.6, iy: 0, y: 4, value: 0.7789161074
ix: 0, x: 1.6, iy: 1, y: 10, value: 0.8200973523
ix: 0, x: 1.6, iy: 2, y: 14, value: 0.8957176666
ix: 0, x: 1.6, iy: 3, y: 18, value: 0.9388893713
ix: 0, x: 1.6, iy: 4, y: 22, value: 0.9315781682
ix: 0, x: 1.6, iy: 5, y: 26, value: 0.9713559332
ix: 0, x: 1.6, iy: 6, y: 30, value: 0.9391629345
ix: 0, x: 1.6, iy: 7, y: 34, value: 0.9577314686
ix: 0, x: 1.6, iy: 8, y: 38, value: 0.9425587151
ix: 0, x: 1.6, iy: 9, y: 42, value: 0.9670160164
ix: 1, x: 1.7, iy: 0, y: 4, value: 0.8469515512
ix: 1, x: 1.7, iy: 1, y: 10, value: 0.8877118706
ix: 1, x: 1.7, iy: 2, y: 14, value: 0.906317489
ix: 1, x: 1.7, iy: 3, y: 18, value: 0.9432625544
ix: 1, x: 1.7, iy: 4, y: 22, value: 0.9399265537
ix: 1, x: 1.7, iy: 5, y: 26, value: 0.9429478773
ix: 1, x: 1.7, iy: 6, y: 30, value: 0.9497225248
ix: 1, x: 1.7, iy: 7, y: 34, value: 0.9442299674
ix: 1, x: 1.7, iy: 8, y: 38, value: 0.9422303213
ix: 1, x: 1.7, iy: 9, y: 42, value: 0.9607127351
ix: 2, x: 1.9, iy: 0, y

In [48]:
bins_eta[:-1]

array([ 1.6,  1.7,  1.9,  2.1,  2.4])

In [49]:
draw(calibFactors_hist, options='COLZ')
# calibFactors_hist.Dump()

In [ ]:
for particle in ['eleA','eleAAA', 'eleAA']:
    for tp_set in ['DEF', 'DEF_em']:
        hByTPset = [histo.h_ptResp for histo in histo_reso_df.loc[tp_set, particle]]
        drawSame(hByTPset, labels, norm=False, text=titles_df.loc[tp_set, particle], v_lines=[1.0])


In [ ]:
for particle in particles:
    for tp_set in ['DEF', 'DEF_em']:
        hByTPset = [histo.h_ptRespVpt for histo in histo_reso_df.loc[tp_set, particle]]
        drawSeveral(hByTPset, labels, options="COLZ", do_profile=True, text=titles_df.loc[tp_set, particle])


In [ ]:
for particle in particles:
    for tp_set in tp_sets:
        hByTPset = [histo.h_ptResVpt.ProjectionY(uuid.uuid4().hex[:6], 6, 10) for histo in histo_reso_df.loc[tp_set, particle]]
        drawSame(hByTPset, labels, norm=True, text=titles_df.loc[tp_set, particle]+' and 10 < p_{t} < 20 GeV')


In [ ]:
for particle in ['ele']:
    for tp_set in ['DEF', 'DEF_em']:
        hByTPset = [histo.h_ptRespVeta for histo in histo_reso_df.loc[tp_set, particle]]
        drawSeveral(hByTPset, labels, options="COLZ", do_profile=True, text=titles_df.loc[tp_set, particle])


In [ ]:
for particle in particles:
    for tp_set in ['DEF', 'DEF_em']:
        hByTPset = [histo.h_ptResp for histo in histo_resoCone_df.loc[tp_set, particle]]
        drawSame(hByTPset, labels, norm=True, text=titles_df.loc[tp_set, particle], v_lines=[1.0])


In [ ]:
for particle in particles:
    for tp_set in ['DEF', 'DEF_em']:
        hByTPset = [histo.h_ptRespVpt for histo in histo_resoCone_df.loc[tp_set, particle]]
        drawSeveral(hByTPset, labels, options="COLZ", do_profile=True, text=titles_df.loc[tp_set, particle])


#### All clusters in DR 0.2 from GEN

In [ ]:
histo_resoCone_df = pd.DataFrame(index=tp_sets, columns=particles)
for tp_set in tp_sets:
    for particle in particles:
        histo_resoCone_df.loc[tp_set][particle] =  [histos.HistoSetReso('{}_{}'.format(tp_set, particle), sample.histo_file).hresoCone for sample in samples]
histo_resoCone_df

In [ ]:
for particle in particles:
    for tp_set in ['DEF', 'DEF_em']:
        hByTPset = [histo.h_ptRes for histo in histo_resoCone_df.loc[tp_set, particle]]
        drawSame(hByTPset, labels, norm=True, text=titles_df.loc[tp_set, particle])


In [ ]:
for particle in particles:
    for tp_set in ['DEF', 'DEF_em']:
        hByTPset = [histo.h_ptResp for histo in histo_resoCone_df.loc[tp_set, particle]]
        drawSame(hByTPset, labels, norm=True, text=titles_df.loc[tp_set, particle])


In [ ]:
for particle in particles:
    for tp_set in ['DEF', 'DEF_em']:
        hByTPset = [histo.h_n010 for histo in histo_resoCone_df.loc[tp_set, particle]]
        drawSame(hByTPset, labels, norm=True, text=titles_df.loc[tp_set, particle])


In [ ]:
for particle in particles:
    for tp_set in ['DEF', 'DEF_em']:
        hByTPset = [histo.h_n025 for histo in histo_resoCone_df.loc[tp_set, particle]]
        drawSame(hByTPset, labels, norm=True, text=titles_df.loc[tp_set, particle])


We now compare the 2 defitnitions (highest pt and all clusters in cone) for the same PU point

In [ ]:
for particle in particles:
    for tp_set in ['DEF', 'DEF_em']:
        hByTPset_best = [histo.h_ptRes for histo in histo_reso_df.loc[tp_set, particle]]
        hByTPset_cone = [histo.h_ptRes for histo in histo_resoCone_df.loc[tp_set, particle]]

        drawSame([hByTPset_best[0], hByTPset_cone[0]], ['PU0 best', 'PU0 cone'], norm=True, text=titles_df.loc[tp_set, particle])
        drawSame([hByTPset_best[1], hByTPset_cone[1]], ['PU200 best', 'PU200 cone'], norm=True, text=titles_df.loc[tp_set, particle])


We now show the behavior of the pt residuals vs pt of the GEN particle

In [ ]:
for algo in algos:
    hByAlgo = [histo.h_ptResVpt for histo in histosAlgos_all.loc[algo].hresoCone]
    #normalize(hclAll_pt35_layer, nevents_pt35)
    drawSeveral(hByAlgo, histosAlgos_all.loc[algo]['labels'], 'COLZ',do_profile=True)
    #print hByAlgo[0].GetName()

In [ ]:
for algo in algos:
    hCl3D_ptResVpt_0 = [histo.h_ptResVpt.ProjectionY(uuid.uuid4().hex[:6], 1, 5) for histo in histosAlgos_all.loc[algo].hresoCone]
    for histo in hCl3D_ptResVpt_0:
        histo.SetTitle('3D cluster reso (GeV) for 1 < pt < 10 GeV')
    #     normalize(hByAlgo, histosAlgos_all.loc[algo]['norm'])
    drawSame(hCl3D_ptResVpt_0, histosAlgos_all.loc[algo]['labels'], norm=True)


In [ ]:
for algo in algos:
    hCl3D_ptResVpt_1 = [histo.h_ptResVpt.ProjectionY(uuid.uuid4().hex[:6], 6, 10) for histo in histosAlgos_all.loc[algo].hresoCone]
    for histo in hCl3D_ptResVpt_1:
        histo.SetTitle('3D cluster reso (GeV) for 10 < pt < 20 GeV')
    #     normalize(hByAlgo, histosAlgos_all.loc[algo]['norm'])
    drawSame(hCl3D_ptResVpt_1, histosAlgos_all.loc[algo]['labels'], norm=True)


In [ ]:
for algo in algos:
    hCl3D_ptResVpt_2 = [histo.h_ptResVpt.ProjectionY(uuid.uuid4().hex[:6], 11, 15) for histo in histosAlgos_all.loc[algo].hresoCone]
    for histo in hCl3D_ptResVpt_2:
        histo.SetTitle('3D cluster reso (GeV) for 20 < pt < 30 GeV')
    #     normalize(hByAlgo, histosAlgos_all.loc[algo]['norm'])
    drawSame(hCl3D_ptResVpt_2, histosAlgos_all.loc[algo]['labels'], norm=True)


In [ ]:
for algo in algos:
    hCl3D_ptResVpt_3 = [histo.h_ptResVpt.ProjectionY(uuid.uuid4().hex[:6], 16, 20) for histo in histosAlgos_all.loc[algo].hresoCone]
    for histo in hCl3D_ptResVpt_3:
        histo.SetTitle('3D cluster reso (GeV) for 30 < pt < 40 GeV')
    #     normalize(hByAlgo, histosAlgos_all.loc[algo]['norm'])
    drawSame(hCl3D_ptResVpt_3, histosAlgos_all.loc[algo]['labels'], norm=True)


In [ ]:
for algo in algos:
    hByAlgo = [histo.h_ptResVeta for histo in histosAlgos_all.loc[algo].hresoCone]
    #normalize(hclAll_pt35_layer, nevents_pt35)
    drawSeveral(hByAlgo, histosAlgos_all.loc[algo]['labels'], 'COLZ',do_profile=True)

In [ ]:
for algo in algos:
    hByAlgo = [histo.h_ptResVnclu for histo in histosAlgos_all.loc[algo].hresoCone]
    #normalize(hclAll_pt35_layer, nevents_pt35)
    drawSeveral(hByAlgo, histosAlgos_all.loc[algo]['labels'], 'COLZ',do_profile=True)

### Energy resolution


In [ ]:


for algo in algos:
    hByAlgo = [histo.h_energyRes for histo in histosAlgos_all.loc[algo].hreso]
    #normalize(hclAll_pt35_layer, nevents_pt35)
    drawSame(hByAlgo, histosAlgos_all.loc[algo]['labels'], norm=True)



In [ ]:

for s_id in range(0, len(samples)):
    labels_bySample = histosAlgos_all['labels'].apply(lambda x: x[s_id])
    hBySample = [histo.h_energyRes for histo in  histosAlgos_all['hreso'].apply(lambda x: x[s_id])]
    drawSame(hBySample, labels_bySample,'hist',logy=True)


## Postion resolution of 2D clusters

In [ ]:
for algo in algos:
    hByAlgo = [histo.h_xResVlayer for histo in histosAlgos_all.loc[algo].hreso2D]
    #normalize(hclAll_pt35_layer, nevents_pt35)
    drawSeveral(hByAlgo, histosAlgos_all.loc[algo]['labels'], 'COLZ',do_profile=True, miny=-2, maxy=2)

In [ ]:
for algo in algos:
    hByAlgo = [histo.h_xResVlayer.ProjectionY(uuid.uuid4().hex[:6], 1, 3) for histo in histosAlgos_all.loc[algo].hreso2D]
    for histo in hByAlgo:
        histo.SetTitle('2D cluster x reso (cm) for layer 1 and 3')
    #     normalize(hByAlgo, histosAlgos_all.loc[algo]['norm'])
    drawSame(hByAlgo, histosAlgos_all.loc[algo]['labels'], norm=True, options='hist')


In [ ]:
for algo in algos:
    hByAlgo = [histo.h_xResVlayer.ProjectionY(uuid.uuid4().hex[:6], 12, 15) for histo in histosAlgos_all.loc[algo].hreso2D]
    for histo in hByAlgo:
        histo.SetTitle('2D cluster x reso (cm) for layer 13 and 15')
    #     normalize(hByAlgo, histosAlgos_all.loc[algo]['norm'])
    drawSame(hByAlgo, histosAlgos_all.loc[algo]['labels'], norm=True, options='hist')


In [ ]:
for algo in algos:
    hByAlgo = [histo.h_yResVlayer for histo in histosAlgos_all.loc[algo].hreso2D]
    #normalize(hclAll_pt35_layer, nevents_pt35)
    drawSeveral(hByAlgo, histosAlgos_all.loc[algo]['labels'], 'COLZ',do_profile=True, miny=-2, maxy=2)